#**Grupo 3**
* Daniel Mattos de Carvalho Sanches da Silva
* Hudson Mesquita Souza
* Tariana de Jesus Gomes Leite

In [0]:
%sh
pip install openpyxl

Collecting openpyxl
 Using cached openpyxl-3.0.10-py2.py3-none-any.whl (242 kB)
Collecting et-xmlfile
 Using cached et_xmlfile-1.1.0-py3-none-any.whl (4.7 kB)
Installing collected packages: et-xmlfile, openpyxl
Successfully installed et-xmlfile-1.1.0 openpyxl-3.0.10
WARNING: You are using pip version 21.0.1; however, version 22.2.2 is available.
You should consider upgrading via the '/databricks/python3/bin/python -m pip install --upgrade pip' command.

In [0]:
# Importação de bibliotecas
from pyspark.sql.functions import *
from pyspark.sql import Row
from pyspark.sql import functions as f
from datetime import date
from datetime import datetime
import pandas as pd
spark.sql("set spark.sql.legacy.timeParserPolicy=LEGACY")

Out[3]: DataFrame[key: string, value: string]

In [0]:
dbutils.fs.ls("/mnt/blobed")

Out[4]: [FileInfo(path='dbfs:/mnt/blobed/BancoBase.csv', name='BancoBase.csv', size=1953699, modificationTime=1657570287000),
 FileInfo(path='dbfs:/mnt/blobed/cases.json', name='cases.json', size=158813, modificationTime=1659021286000),
 FileInfo(path='dbfs:/mnt/blobed/dClientes.csv', name='dClientes.csv', size=29829, modificationTime=1657570285000),
 FileInfo(path='dbfs:/mnt/blobed/dCompras.csv', name='dCompras.csv', size=272422, modificationTime=1657570286000),
 FileInfo(path='dbfs:/mnt/blobed/dProdutos.csv', name='dProdutos.csv', size=198630, modificationTime=1657654422000),
 FileInfo(path='dbfs:/mnt/blobed/fVendas.csv', name='fVendas.csv', size=525994, modificationTime=1657654410000),
 FileInfo(path='dbfs:/mnt/blobed/modulo_02/', name='modulo_02/', size=0, modificationTime=0)]

#**Concessionária**

Desde o começo deste projeto foi no informado que estaríamos trabalhando com dados de vendas de carros, portanto já pudemos inferir que:
*   A Data seria uma uma coluna muito importante para o projeto, pois a venda por período de tempo (seja qual o dia da semana ou durante feriados, por exemplo) pode ser uma maneira significativa de aumentar as vendas;
*   A quantidade de vendas por Marca e/ou Modelo;
*   Dentre outras que poderiam ser solicitadas.

#**Data_feriado**
Neste bloco foram disponibilizados dois CSVs para realizar a limpeza e a junção em um único dataframe contendo as colunas:
*   Data;
*   Numero - com inteiros de 1 a 7 representando os dias da semana;
*   Tipo - Útil, feriado (com o nome) e fim de semana;
*   0-1 - 0 para fins de semana e feriados e 1 para dias úteis.

__________________

**Calendário**
* A coluna Data era do tipo string - converção para o tipo date com a máscara dd/MM/yyyy

**Feriado**
* Ao final do CSV havia algumas colunas com informações nulas e sem relevância para o projeto, portanto houve a remoção deles
* A coluna Data era do tipo string - converção para o tipo date com a máscara dd/MM/yyyy

Depois da limpeza e tipagem, foi feito um letf join de Data e Feriado (nesta ordem) e então:
* Transformação da coluna Data em Timestamp, criação da coluna Numero usando a função date_format passando a coluna Data e o parâmetro "u", que mostra o dia da semana em nº, em que 1 é seg. e 7 é dom;
* Utilização a cláusula when, comparação dos valores da coluna Numero para o preenchimento dos valores da coluna Tipo;
* Utilizando a cláusula when, comparação dos valores da coluna Tipo para preencher os valores da coluna 0-1 (se for 'Útil' seta 1; senão seta 0);
* E por fim, tipagem dos dados: Data para tipo date e Numero e 0-1 para tipo int.

In [0]:
#Leitura dos CSVs
calendario = spark.read.options(sep=";", header=True, encoding = "UTF-8").csv("/mnt/blobed/modulo_02/calendario/calendario.csv")
feriados = spark.read.options(sep=";", header=True, encoding = "UTF-8").csv("/mnt/blobed/modulo_02/calendario/feriados_nacionais.csv")

display(calendario)
display(feriados)

Data 30/06/2016 00:00 01/07/2016 00:00 02/07/2016 00:00 03/07/2016 00:00 04/07/2016 00:00 05/07/2016 00:00 06/07/2016 00:00 07/07/2016 00:00 08/07/2016 00:00 09/07/2016 00:00 10/07/2016 00:00 11/07/2016 00:00 12/07/2016 00:00 13/07/2016 00:00 14/07/2016 00:00 15/07/2016 00:00 16/07/2016 00:00 17/07/2016 00:00 18/07/2016 00:00 19/07/2016 00:00 20/07/2016 00:00 21/07/2016 00:00 22/07/2016 00:00 23/07/2016 00:00 24/07/2016 00:00 25/07/2016 00:00 26/07/2016 00:00 27/07/2016 00:00 28/07/2016 00:00 29/07/2016 00:00 30/07/2016 00:00 31/07/2016 00:00 01/08/2016 00:00 02/08/2016 00:00 03/08/2016 00:00 04/08/2016 00:00 05/08/2016 00:00 06/08/2016 00:00 07/08/2016 00:00 08/08/2016 00:00 09/08/2016 00:00 10/08/2016 00:00 11/08/2016 00:00 12/08/2016 00:00 13/08/2016 00:00 14/08/2016 00:00 15/08/2016 00:00 16/08/2016 00:00 17/08/2016 00:00 18/08/2016 00:00 19/08/2016 00:00 20/08/2016 00:00 21/08/2016 00:00 22/08/2016 00:00 23/08/2016 00:00 24/08/2016 00:00 25/08/2016 00:00 26/08/2016 00:00 27/08/2016 00:00 28/08/2016 00:00 29/08/2016 00:00 30/08/2016 00:00 31/08/2016 00:00 01/09/2016 00:00 02/09/2016 00:00 03/09/2016 00:00 04/09/2016 00:00 05/09/2016 00:00 06/09/2016 00:00 07/09/2016 00:00 08/09/2016 00:00 09/09/2016 00:00 10/09/2016 00:00 11/09/2016 00:00 12/09/2016 00:00 13/09/2016 00:00 14/09/2016 00:00 15/09/2016 00:00 16/09/2016 00:00 17/09/2016 00:00 18/09/2016 00:00 19/09/2016 00:00 20/09/2016 00:00 21/09/2016 00:00 22/09/2016 00:00 23/09/2016 00:00 24/09/2016 00:00 25/09/2016 00:00 26/09/2016 00:00 27/09/2016 00:00 28/09/2016 00:00 29/09/2016 00:00 30/09/2016 00:00 01/10/2016 00:00 02/10/2016 00:00 03/10/2016 00:00 04/10/2016 00:00 05/10/2016 00:00 06/10/2016 00:00 07/10/2016 00:00 08/10/2016 00:00 09/10/2016 00:00 10/10/2016 00:00 11/10/2016 00:00 12/10/2016 00:00 13/10/2016 00:00 14/10/2016 00:00 15/10/2016 00:00 16/10/2016 00:00 17/10/2016 00:00 18/10/2016 00:00 19/10/2016 00:00 20/10/2016 00:00 21/10/2016 00:00 22/10/2016 00:00 23/10/2016 00:00 24/10/2016 00:00 25/10/2016 00:00 26/10/2016 00:00 27/10/2016 00:00 28/10/2016 00:00 29/10/2016 00:00 30/10/2016 00:00 31/10/2016 00:00 01/11/2016 00:00 02/11/2016 00:00 03/11/2016 00:00 04/11/2016 00:00 05/11/2016 00:00 06/11/2016 00:00 07/11/2016 00:00 08/11/2016 00:00 09/11/2016 00:00 10/11/2016 00:00 11/11/2016 00:00 12/11/2016 00:00 13/11/2016 00:00 14/11/2016 00:00 15/11/2016 00:00 16/11/2016 00:00 17/11/2016 00:00 18/11/2016 00:00 19/11/2016 00:00 20/11/2016 00:00 21/11/2016 00:00 22/11/2016 00:00 23/11/2016 00:00 24/11/2016 00:00 25/11/2016 00:00 26/11/2016 00:00 27/11/2016 00:00 28/11/2016 00:00 29/11/2016 00:00 30/11/2016 00:00 01/12/2016 00:00 02/12/2016 00:00 03/12/2016 00:00 04/12/2016 00:00 05/12/2016 00:00 06/12/2016 00:00 07/12/2016 00:00 08/12/2016 00:00 09/12/2016 00:00 10/12/2016 00:00 11/12/2016 00:00 12/12/2016 00:00 13/12/2016 00:00 14/12/2016 00:00 15/12/2016 00:00 16/12/2016 00:00 17/12/2016 00:00 18/12/2016 00:00 19/12/2016 00:00 20/12/2016 00:00 21/12/2016 00:00 22/12/2016 00:00 23/12/2016 00:00 24/12/2016 00:00 25/12/2016 00:00 26/12/2016 00:00 27/12/2016 00:00 28/12/2016 00:00 29/12/2016 00:00 30/12/2016 00:00 31/12/2016 00:00 01/01/2017 00:00 02/01/2017 00:00 03/01/2017 00:00 04/01/2017 00:00 05/01/2017 00:00 06/01/2017 00:00 07/01/2017 00:00 08/01/2017 00:00 09/01/2017 00:00 10/01/2017 00:00 11/01/2017 00:00 12/01/2017 00:00 13/01/2017 00:00 14/01/2017 00:00 15/01/2017 00:00 16/01/2017 00:00 17/01/2017 00:00 18/01/2017 00:00 19/01/2017 00:00 20/01/2017 00:00 21/01/2017 00:00 22/01/2017 00:00 23/01/2017 00:00 24/01/2017 00:00 25/01/2017 00:00 26/01/2017 00:00 27/01/2017 00:00 28/01/2017 00:00 29/01/2017 00:00 30/01/2017 00:00 31/01/2017 00:00 01/02/2017 00:00 02/02/2017 00:00 03/02/2017 00:00 04/02/2017 00:00 05/02/2017 00:00 06/02/2017 00:00 07/02/2017 00:00 08/02/2017 00:00 09/02/2017 00:00 10/02/2017 00:00 11/02/2017 00:00 12/02/2017 00:00 13/02/2017 00:00 14/02/2017 00:00 15/02/2017 00:00 16/02/2017 00:00 17/02/2017 00:00 18/02/2017 00:00 19/02/2017 00:00 

Data Dia da Semana Feriado 01/01/2001 segunda-feira Confraternização Universal 26/02/2001 segunda-feira Carnaval 27/02/2001 terça-feira Carnaval 13/04/2001 sexta-feira Paixão de Cristo 21/04/2001 sábado Tiradentes 01/05/2001 terça-feira Dia do Trabalho 14/06/2001 quinta-feira Corpus Christi 07/09/2001 sexta-feira Independência do Brasil 12/10/2001 sexta-feira Nossa Sr.a Aparecida - Padroeira do Brasil 02/11/2001 sexta-feira Finados 15/11/2001 quinta-feira Proclamação da República 25/12/2001 terça-feira Natal 01/01/2002 terça-feira Confraternização Universal 11/02/2002 segunda-feira Carnaval 12/02/2002 terça-feira Carnaval 29/03/2002 sexta-feira Paixão de Cristo 21/04/2002 domingo Tiradentes 01/05/2002 quarta-feira Dia do Trabalho 30/05/2002 quinta-feira Corpus Christi 07/09/2002 sábado Independência do Brasil 12/10/2002 sábado Nossa Sr.a Aparecida - Padroeira do Brasil 02/11/2002 sábado Finados 15/11/2002 sexta-feira Proclamação da República 25/12/2002 quarta-feira Natal 01/01/2003 quarta-feira Confraternização Universal 03/03/2003 segunda-feira Carnaval 04/03/2003 terça-feira Carnaval 18/04/2003 sexta-feira Paixão de Cristo 21/04/2003 segunda-feira Tiradentes 01/05/2003 quinta-feira Dia do Trabalho 19/06/2003 quinta-feira Corpus Christi 07/09/2003 domingo Independência do Brasil 12/10/2003 domingo Nossa Sr.a Aparecida - Padroeira do Brasil 02/11/2003 domingo Finados 15/11/2003 sábado Proclamação da República 25/12/2003 quinta-feira Natal 01/01/2004 quinta-feira Confraternização Universal 23/02/2004 segunda-feira Carnaval 24/02/2004 terça-feira Carnaval 09/04/2004 sexta-feira Paixão de Cristo 21/04/2004 quarta-feira Tiradentes 01/05/2004 sábado Dia do Trabalho 10/06/2004 quinta-feira Corpus Christi 07/09/2004 terça-feira Independência do Brasil 12/10/2004 terça-feira Nossa Sr.a Aparecida - Padroeira do Brasil 02/11/2004 terça-feira Finados 15/11/2004 segunda-feira Proclamação da República 25/12/2004 sábado Natal 01/01/2005 sábado Confraternização Universal 07/02/2005 segunda-feira Carnaval 08/02/2005 terça-feira Carnaval 25/03/2005 sexta-feira Paixão de Cristo 21/04/2005 quinta-feira Tiradentes 01/05/2005 domingo Dia do Trabalho 26/05/2005 quinta-feira Corpus Christi 07/09/2005 quarta-feira Independência do Brasil 12/10/2005 quarta-feira Nossa Sr.a Aparecida - Padroeira do Brasil 02/11/2005 quarta-feira Finados 15/11/2005 terça-feira Proclamação da República 25/12/2005 domingo Natal 01/01/2006 domingo Confraternização Universal 27/02/2006 segunda-feira Carnaval 28/02/2006 terça-feira Carnaval 14/04/2006 sexta-feira Paixão de Cristo 21/04/2006 sexta-feira Tiradentes 01/05/2006 segunda-feira Dia do Trabalho 15/06/2006 quinta-feira Corpus Christi 07/09/2006 quinta-feira Independência do Brasil 12/10/2006 quinta-feira Nossa Sr.a Aparecida - Padroeira do Brasil 02/11/2006 quinta-feira Finados 15/11/2006 quarta-feira Proclamação da República 25/12/2006 segunda-feira Natal 01/01/2007 segunda-feira Confraternização Universal 19/02/2007 segunda-feira Carnaval 20/02/2007 terça-feira Carnaval 06/04/2007 sexta-feira Paixão de Cristo 21/04/2007 sábado Tiradentes 01/05/2007 terça-feira Dia do Trabalho 07/06/2007 quinta-feira Corpus Christi 07/09/2007 sexta-feira Independência do Brasil 12/10/2007 sexta-feira Nossa Sr.a Aparecida - Padroeira do Brasil 02/11/2007 sexta-feira Finados 15/11/2007 quinta-feira Proclamação da República 25/12/2007 terça-feira Natal 01/01/2008 terça-feira Confraternização Universal 04/02/2008 segunda-feira Carnaval 05/02/2008 terça-feira Carnaval 21/03/2008 sexta-feira Paixão de Cristo 21/04/2008 segunda-feira Tiradentes 01/05/2008 quinta-feira Dia do Trabalho 22/05/2008 quinta-feira Corpus Christi 07/09/2008 domingo Independência do Brasil 12/10/2008 domingo Nossa Sr.a Aparecida - Padroeira do Brasil 02/11/2008 domingo Finados 15/11/2008 sábado Proclamação da República 25/12/2008 quinta-feira Natal 01/01/2009 quinta-feira Confraternização Universal 23/02/2009 segunda-feira Carnaval 24/02/2009 terça-feira Carnaval 1

In [0]:
#Converte a coluna Data para o tipo date e guarda em calend
calend = calendario.withColumn("Data", f.to_date(f.to_timestamp(col("Data"), "dd/MM/yyyy")))
display(calend)

Data 2016-06-30 2016-07-01 2016-07-02 2016-07-03 2016-07-04 2016-07-05 2016-07-06 2016-07-07 2016-07-08 2016-07-09 2016-07-10 2016-07-11 2016-07-12 2016-07-13 2016-07-14 2016-07-15 2016-07-16 2016-07-17 2016-07-18 2016-07-19 2016-07-20 2016-07-21 2016-07-22 2016-07-23 2016-07-24 2016-07-25 2016-07-26 2016-07-27 2016-07-28 2016-07-29 2016-07-30 2016-07-31 2016-08-01 2016-08-02 2016-08-03 2016-08-04 2016-08-05 2016-08-06 2016-08-07 2016-08-08 2016-08-09 2016-08-10 2016-08-11 2016-08-12 2016-08-13 2016-08-14 2016-08-15 2016-08-16 2016-08-17 2016-08-18 2016-08-19 2016-08-20 2016-08-21 2016-08-22 2016-08-23 2016-08-24 2016-08-25 2016-08-26 2016-08-27 2016-08-28 2016-08-29 2016-08-30 2016-08-31 2016-09-01 2016-09-02 2016-09-03 2016-09-04 2016-09-05 2016-09-06 2016-09-07 2016-09-08 2016-09-09 2016-09-10 2016-09-11 2016-09-12 2016-09-13 2016-09-14 2016-09-15 2016-09-16 2016-09-17 2016-09-18 2016-09-19 2016-09-20 2016-09-21 2016-09-22 2016-09-23 2016-09-24 2016-09-25 2016-09-26 2016-09-27 2016-09-28 2016-09-29 2016-09-30 2016-10-01 2016-10-02 2016-10-03 2016-10-04 2016-10-05 2016-10-06 2016-10-07 2016-10-08 2016-10-09 2016-10-10 2016-10-11 2016-10-12 2016-10-13 2016-10-14 2016-10-15 2016-10-16 2016-10-17 2016-10-18 2016-10-19 2016-10-20 2016-10-21 2016-10-22 2016-10-23 2016-10-24 2016-10-25 2016-10-26 2016-10-27 2016-10-28 2016-10-29 2016-10-30 2016-10-31 2016-11-01 2016-11-02 2016-11-03 2016-11-04 2016-11-05 2016-11-06 2016-11-07 2016-11-08 2016-11-09 2016-11-10 2016-11-11 2016-11-12 2016-11-13 2016-11-14 2016-11-15 2016-11-16 2016-11-17 2016-11-18 2016-11-19 2016-11-20 2016-11-21 2016-11-22 2016-11-23 2016-11-24 2016-11-25 2016-11-26 2016-11-27 2016-11-28 2016-11-29 2016-11-30 2016-12-01 2016-12-02 2016-12-03 2016-12-04 2016-12-05 2016-12-06 2016-12-07 2016-12-08 2016-12-09 2016-12-10 2016-12-11 2016-12-12 2016-12-13 2016-12-14 2016-12-15 2016-12-16 2016-12-17 2016-12-18 2016-12-19 2016-12-20 2016-12-21 2016-12-22 2016-12-23 2016-12-24 2016-12-25 2016-12-26 2016-12-27 2016-12-28 2016-12-29 2016-12-30 2016-12-31 2017-01-01 2017-01-02 2017-01-03 2017-01-04 2017-01-05 2017-01-06 2017-01-07 2017-01-08 2017-01-09 2017-01-10 2017-01-11 2017-01-12 2017-01-13 2017-01-14 2017-01-15 2017-01-16 2017-01-17 2017-01-18 2017-01-19 2017-01-20 2017-01-21 2017-01-22 2017-01-23 2017-01-24 2017-01-25 2017-01-26 2017-01-27 2017-01-28 2017-01-29 2017-01-30 2017-01-31 2017-02-01 2017-02-02 2017-02-03 2017-02-04 2017-02-05 2017-02-06 2017-02-07 2017-02-08 2017-02-09 2017-02-10 2017-02-11 2017-02-12 2017-02-13 2017-02-14 2017-02-15 2017-02-16 2017-02-17 2017-02-18 2017-02-19 2017-02-20 2017-02-21 2017-02-22 2017-02-23 2017-02-24 2017-02-25 2017-02-26 2017-02-27 2017-02-28 2017-03-01 2017-03-02 2017-03-03 2017-03-04 2017-03-05 2017-03-06 2017-03-07 2017-03-08 2017-03-09 2017-03-10 2017-03-11 2017-03-12 2017-03-13 2017-03-14 2017-03-15 2017-03-16 2017-03-17 2017-03-18 2017-03-19 2017-03-20 2017-03-21 2017-03-22 2017-03-23 2017-03-24 2017-03-25 2017-03-26 2017-03-27 2017-03-28 2017-03-29 2017-03-30 2017-03-31 2017-04-01 2017-04-02 2017-04-03 2017-04-04 2017-04-05 2017-04-06 2017-04-07 2017-04-08 2017-04-09 2017-04-10 2017-04-11 2017-04-12 2017-04-13 2017-04-14 2017-04-15 2017-04-16 2017-04-17 2017-04-18 2017-04-19 2017-04-20 2017-04-21 2017-04-22 2017-04-23 2017-04-24 2017-04-25 2017-04-26 2017-04-27 2017-04-28 2017-04-29 2017-04-30 2017-05-01 2017-05-02 2017-05-03 2017-05-04 2017-05-05 2017-05-06 2017-05-07 2017-05-08 2017-05-09 2017-05-10 2017-05-11 2017-05-12 2017-05-13 2017-05-14 2017-05-15 2017-05-16 2017-05-17 2017-05-18 2017-05-19 2017-05-20 2017-05-21 2017-05-22 2017-05-23 2017-05-24 2017-05-25 2017-05-26 2017-05-27 2017-05-28 2017-05-29 2017-05-30 2017-05-31 2017-06-01 2017-06-02 2017-06-03 2017-06-04 2017-06-05 2017-06-06 2017-06-07 2017-06-08 2017-06-09 2017-06-10 2017-06-11 2017-06-12 2017-06-13 2017-06-14 2017-06-15 2017-06-16 2017-06-17 2017-06-18 2017-06-19 2017-06-20 2017-06-21 2017-06-22 2017-06-23 2017-06-24 2017-06-25 2017-06-26 2017-06-27 20

In [0]:
#Remove os nulos de feriados e guarda em feriados_nn
feriados_nn = feriados.na.drop(how="any") #how = any dropa se algum dos valores for nulo
feriados_nn = feriados_nn.withColumn("Data", f.to_date(f.to_timestamp(col("Data"), "dd/MM/yyyy")))
display(feriados_nn)

Data Dia da Semana Feriado 2001-01-01 segunda-feira Confraternização Universal 2001-02-26 segunda-feira Carnaval 2001-02-27 terça-feira Carnaval 2001-04-13 sexta-feira Paixão de Cristo 2001-04-21 sábado Tiradentes 2001-05-01 terça-feira Dia do Trabalho 2001-06-14 quinta-feira Corpus Christi 2001-09-07 sexta-feira Independência do Brasil 2001-10-12 sexta-feira Nossa Sr.a Aparecida - Padroeira do Brasil 2001-11-02 sexta-feira Finados 2001-11-15 quinta-feira Proclamação da República 2001-12-25 terça-feira Natal 2002-01-01 terça-feira Confraternização Universal 2002-02-11 segunda-feira Carnaval 2002-02-12 terça-feira Carnaval 2002-03-29 sexta-feira Paixão de Cristo 2002-04-21 domingo Tiradentes 2002-05-01 quarta-feira Dia do Trabalho 2002-05-30 quinta-feira Corpus Christi 2002-09-07 sábado Independência do Brasil 2002-10-12 sábado Nossa Sr.a Aparecida - Padroeira do Brasil 2002-11-02 sábado Finados 2002-11-15 sexta-feira Proclamação da República 2002-12-25 quarta-feira Natal 2003-01-01 quarta-feira Confraternização Universal 2003-03-03 segunda-feira Carnaval 2003-03-04 terça-feira Carnaval 2003-04-18 sexta-feira Paixão de Cristo 2003-04-21 segunda-feira Tiradentes 2003-05-01 quinta-feira Dia do Trabalho 2003-06-19 quinta-feira Corpus Christi 2003-09-07 domingo Independência do Brasil 2003-10-12 domingo Nossa Sr.a Aparecida - Padroeira do Brasil 2003-11-02 domingo Finados 2003-11-15 sábado Proclamação da República 2003-12-25 quinta-feira Natal 2004-01-01 quinta-feira Confraternização Universal 2004-02-23 segunda-feira Carnaval 2004-02-24 terça-feira Carnaval 2004-04-09 sexta-feira Paixão de Cristo 2004-04-21 quarta-feira Tiradentes 2004-05-01 sábado Dia do Trabalho 2004-06-10 quinta-feira Corpus Christi 2004-09-07 terça-feira Independência do Brasil 2004-10-12 terça-feira Nossa Sr.a Aparecida - Padroeira do Brasil 2004-11-02 terça-feira Finados 2004-11-15 segunda-feira Proclamação da República 2004-12-25 sábado Natal 2005-01-01 sábado Confraternização Universal 2005-02-07 segunda-feira Carnaval 2005-02-08 terça-feira Carnaval 2005-03-25 sexta-feira Paixão de Cristo 2005-04-21 quinta-feira Tiradentes 2005-05-01 domingo Dia do Trabalho 2005-05-26 quinta-feira Corpus Christi 2005-09-07 quarta-feira Independência do Brasil 2005-10-12 quarta-feira Nossa Sr.a Aparecida - Padroeira do Brasil 2005-11-02 quarta-feira Finados 2005-11-15 terça-feira Proclamação da República 2005-12-25 domingo Natal 2006-01-01 domingo Confraternização Universal 2006-02-27 segunda-feira Carnaval 2006-02-28 terça-feira Carnaval 2006-04-14 sexta-feira Paixão de Cristo 2006-04-21 sexta-feira Tiradentes 2006-05-01 segunda-feira Dia do Trabalho 2006-06-15 quinta-feira Corpus Christi 2006-09-07 quinta-feira Independência do Brasil 2006-10-12 quinta-feira Nossa Sr.a Aparecida - Padroeira do Brasil 2006-11-02 quinta-feira Finados 2006-11-15 quarta-feira Proclamação da República 2006-12-25 segunda-feira Natal 2007-01-01 segunda-feira Confraternização Universal 2007-02-19 segunda-feira Carnaval 2007-02-20 terça-feira Carnaval 2007-04-06 sexta-feira Paixão de Cristo 2007-04-21 sábado Tiradentes 2007-05-01 terça-feira Dia do Trabalho 2007-06-07 quinta-feira Corpus Christi 2007-09-07 sexta-feira Independência do Brasil 2007-10-12 sexta-feira Nossa Sr.a Aparecida - Padroeira do Brasil 2007-11-02 sexta-feira Finados 2007-11-15 quinta-feira Proclamação da República 2007-12-25 terça-feira Natal 2008-01-01 terça-feira Confraternização Universal 2008-02-04 segunda-feira Carnaval 2008-02-05 terça-feira Carnaval 2008-03-21 sexta-feira Paixão de Cristo 2008-04-21 segunda-feira Tiradentes 2008-05-01 quinta-feira Dia do Trabalho 2008-05-22 quinta-feira Corpus Christi 2008-09-07 domingo Independência do Brasil 2008-10-12 domingo Nossa Sr.a Aparecida - Padroeira do Brasil 2008-11-02 domingo Finados 2008-11-15 sábado Proclamação da República 2008-12-25 quinta-feira Natal 2009-01-01 quinta-feira Confraternização Universal 2009-02-23 segunda-feira Carnaval 2009-02-24 terça-feira Carnaval 2

In [0]:
#Junção dos 2 frames pegando o que tem do da esquerda e em comum entre os 2
data_feriado = calend.join(feriados_nn, on=['Data'], how='left').orderBy('Data')
display(data_feriado)

Data Dia da Semana Feriado 2016-06-30 null null 2016-07-01 null null 2016-07-02 null null 2016-07-03 null null 2016-07-04 null null 2016-07-05 null null 2016-07-06 null null 2016-07-07 null null 2016-07-08 null null 2016-07-09 null null 2016-07-10 null null 2016-07-11 null null 2016-07-12 null null 2016-07-13 null null 2016-07-14 null null 2016-07-15 null null 2016-07-16 null null 2016-07-17 null null 2016-07-18 null null 2016-07-19 null null 2016-07-20 null null 2016-07-21 null null 2016-07-22 null null 2016-07-23 null null 2016-07-24 null null 2016-07-25 null null 2016-07-26 null null 2016-07-27 null null 2016-07-28 null null 2016-07-29 null null 2016-07-30 null null 2016-07-31 null null 2016-08-01 null null 2016-08-02 null null 2016-08-03 null null 2016-08-04 null null 2016-08-05 null null 2016-08-06 null null 2016-08-07 null null 2016-08-08 null null 2016-08-09 null null 2016-08-10 null null 2016-08-11 null null 2016-08-12 null null 2016-08-13 null null 2016-08-14 null null 2016-08-15 null null 2016-08-16 null null 2016-08-17 null null 2016-08-18 null null 2016-08-19 null null 2016-08-20 null null 2016-08-21 null null 2016-08-22 null null 2016-08-23 null null 2016-08-24 null null 2016-08-25 null null 2016-08-26 null null 2016-08-27 null null 2016-08-28 null null 2016-08-29 null null 2016-08-30 null null 2016-08-31 null null 2016-09-01 null null 2016-09-02 null null 2016-09-03 null null 2016-09-04 null null 2016-09-05 null null 2016-09-06 null null 2016-09-07 quarta-feira Independência do Brasil 2016-09-08 null null 2016-09-09 null null 2016-09-10 null null 2016-09-11 null null 2016-09-12 null null 2016-09-13 null null 2016-09-14 null null 2016-09-15 null null 2016-09-16 null null 2016-09-17 null null 2016-09-18 null null 2016-09-19 null null 2016-09-20 null null 2016-09-21 null null 2016-09-22 null null 2016-09-23 null null 2016-09-24 null null 2016-09-25 null null 2016-09-26 null null 2016-09-27 null null 2016-09-28 null null 2016-09-29 null null 2016-09-30 null null 2016-10-01 null null 2016-10-02 null null 2016-10-03 null null 2016-10-04 null null 2016-10-05 null null 2016-10-06 null null 2016-10-07 null null 2016-10-08 null null 2016-10-09 null null 2016-10-10 null null 2016-10-11 null null 2016-10-12 quarta-feira Nossa Sr.a Aparecida - Padroeira do Brasil 2016-10-13 null null 2016-10-14 null null 2016-10-15 null null 2016-10-16 null null 2016-10-17 null null 2016-10-18 null null 2016-10-19 null null 2016-10-20 null null 2016-10-21 null null 2016-10-22 null null 2016-10-23 null null 2016-10-24 null null 2016-10-25 null null 2016-10-26 null null 2016-10-27 null null 2016-10-28 null null 2016-10-29 null null 2016-10-30 null null 2016-10-31 null null 2016-11-01 null null 2016-11-02 quarta-feira Finados 2016-11-03 null null 2016-11-04 null null 2016-11-05 null null 2016-11-06 null null 2016-11-07 null null 2016-11-08 null null 2016-11-09 null null 2016-11-10 null null 2016-11-11 null null 2016-11-12 null null 2016-11-13 null null 2016-11-14 null null 2016-11-15 terça-feira Proclamação da República 2016-11-16 null null 2016-11-17 null null 2016-11-18 null null 2016-11-19 null null 2016-11-20 null null 2016-11-21 null null 2016-11-22 null null 2016-11-23 null null 2016-11-24 null null 2016-11-25 null null 2016-11-26 null null 2016-11-27 null null 2016-11-28 null null 2016-11-29 null null 2016-11-30 null null 2016-12-01 null null 2016-12-02 null null 2016-12-03 null null 2016-12-04 null null 2016-12-05 null null 2016-12-06 null null 2016-12-07 null null 2016-12-08 null null 2016-12-09 null null 2016-12-10 null null 2016-12-11 null null 2016-12-12 null null 2016-12-13 null null 2016-12-14 null null 2016-12-15 null null 2016-12-16 null null 2016-12-17 null null 2016-12-18 null null 2016-12-19 null null 2016-12-20 null null 2016-12-21 null null 2016-12-22 null null 2016-12-23 null null 2016-12-24 null null 2016-12-25 domingo Natal 2016-12-26 null null 2016-12-27 null null 2016-12-28 null null 2016-12-29 null null 2016-12-30 null

In [0]:
#o padrão de formatação de data é usado para obter o dia da semana em um número. por exemplo 1 para segunda-feira e 7 para domingo
#u – o padrão de formatação de data é usado para obter o dia da semana em um número. por exemplo 1 para segunda-feira e 7 para domingo
data_feriado = data_feriado.withColumn("Data", \
    to_timestamp(col("Data")))\
    .withColumn("Numero", date_format(col("Data"), "u"))


In [0]:
#Cria a coluna 'Tipo' e a preenche segundo a cláusula when
data_feriado = data_feriado.withColumn("Tipo", \
                                       when((data_feriado.Numero == '6') | (data_feriado.Numero == '7'), 'Fim de Semana')\
                                       .when((data_feriado.Feriado.isNull()), 'Útil')\
                                       .otherwise(data_feriado.Feriado)
                                      )
display(data_feriado)

Data Dia da Semana Feriado Numero Tipo 2016-06-30T00:00:00.000+0000 null null 4 Útil 2016-07-01T00:00:00.000+0000 null null 5 Útil 2016-07-02T00:00:00.000+0000 null null 6 Fim de Semana 2016-07-03T00:00:00.000+0000 null null 7 Fim de Semana 2016-07-04T00:00:00.000+0000 null null 1 Útil 2016-07-05T00:00:00.000+0000 null null 2 Útil 2016-07-06T00:00:00.000+0000 null null 3 Útil 2016-07-07T00:00:00.000+0000 null null 4 Útil 2016-07-08T00:00:00.000+0000 null null 5 Útil 2016-07-09T00:00:00.000+0000 null null 6 Fim de Semana 2016-07-10T00:00:00.000+0000 null null 7 Fim de Semana 2016-07-11T00:00:00.000+0000 null null 1 Útil 2016-07-12T00:00:00.000+0000 null null 2 Útil 2016-07-13T00:00:00.000+0000 null null 3 Útil 2016-07-14T00:00:00.000+0000 null null 4 Útil 2016-07-15T00:00:00.000+0000 null null 5 Útil 2016-07-16T00:00:00.000+0000 null null 6 Fim de Semana 2016-07-17T00:00:00.000+0000 null null 7 Fim de Semana 2016-07-18T00:00:00.000+0000 null null 1 Útil 2016-07-19T00:00:00.000+0000 null null 2 Útil 2016-07-20T00:00:00.000+0000 null null 3 Útil 2016-07-21T00:00:00.000+0000 null null 4 Útil 2016-07-22T00:00:00.000+0000 null null 5 Útil 2016-07-23T00:00:00.000+0000 null null 6 Fim de Semana 2016-07-24T00:00:00.000+0000 null null 7 Fim de Semana 2016-07-25T00:00:00.000+0000 null null 1 Útil 2016-07-26T00:00:00.000+0000 null null 2 Útil 2016-07-27T00:00:00.000+0000 null null 3 Útil 2016-07-28T00:00:00.000+0000 null null 4 Útil 2016-07-29T00:00:00.000+0000 null null 5 Útil 2016-07-30T00:00:00.000+0000 null null 6 Fim de Semana 2016-07-31T00:00:00.000+0000 null null 7 Fim de Semana 2016-08-01T00:00:00.000+0000 null null 1 Útil 2016-08-02T00:00:00.000+0000 null null 2 Útil 2016-08-03T00:00:00.000+0000 null null 3 Útil 2016-08-04T00:00:00.000+0000 null null 4 Útil 2016-08-05T00:00:00.000+0000 null null 5 Útil 2016-08-06T00:00:00.000+0000 null null 6 Fim de Semana 2016-08-07T00:00:00.000+0000 null null 7 Fim de Semana 2016-08-08T00:00:00.000+0000 null null 1 Útil 2016-08-09T00:00:00.000+0000 null null 2 Útil 2016-08-10T00:00:00.000+0000 null null 3 Útil 2016-08-11T00:00:00.000+0000 null null 4 Útil 2016-08-12T00:00:00.000+0000 null null 5 Útil 2016-08-13T00:00:00.000+0000 null null 6 Fim de Semana 2016-08-14T00:00:00.000+0000 null null 7 Fim de Semana 2016-08-15T00:00:00.000+0000 null null 1 Útil 2016-08-16T00:00:00.000+0000 null null 2 Útil 2016-08-17T00:00:00.000+0000 null null 3 Útil 2016-08-18T00:00:00.000+0000 null null 4 Útil 2016-08-19T00:00:00.000+0000 null null 5 Útil 2016-08-20T00:00:00.000+0000 null null 6 Fim de Semana 2016-08-21T00:00:00.000+0000 null null 7 Fim de Semana 2016-08-22T00:00:00.000+0000 null null 1 Útil 2016-08-23T00:00:00.000+0000 null null 2 Útil 2016-08-24T00:00:00.000+0000 null null 3 Útil 2016-08-25T00:00:00.000+0000 null null 4 Útil 2016-08-26T00:00:00.000+0000 null null 5 Útil 2016-08-27T00:00:00.000+0000 null null 6 Fim de Semana 2016-08-28T00:00:00.000+0000 null null 7 Fim de Semana 2016-08-29T00:00:00.000+0000 null null 1 Útil 2016-08-30T00:00:00.000+0000 null null 2 Útil 2016-08-31T00:00:00.000+0000 null null 3 Útil 2016-09-01T00:00:00.000+0000 null null 4 Útil 2016-09-02T00:00:00.000+0000 null null 5 Útil 2016-09-03T00:00:00.000+0000 null null 6 Fim de Semana 2016-09-04T00:00:00.000+0000 null null 7 Fim de Semana 2016-09-05T00:00:00.000+0000 null null 1 Útil 2016-09-06T00:00:00.000+0000 null null 2 Útil 2016-09-07T00:00:00.000+0000 quarta-feira Independência do Brasil 3 Independência do Brasil 2016-09-08T00:00:00.000+0000 null null 4 Útil 2016-09-09T00:00:00.000+0000 null null 5 Útil 2016-09-10T00:00:00.000+0000 null null 6 Fim de Semana 2016-09-11T00:00:00.000+0000 null null 7 Fim de Semana 2016-09-12T00:00:00.000+0000 null null 1 Útil 2016-09-13T00:00:00.000+0000 null null 2 Útil 2016-09-14T00:00:00.000+0000 null null 3 Útil 2016-09-15T00:00:00.000+0000 null null 4 Útil 2016-09-16T00:00:00.000+0000 null null 5 Útil 2016-09-17T00:00:00.000+0000 null null 6 Fim de Semana 2016-09-18T00:00:00.000+0000

In [0]:
#Cria a coluna '0-1' e a preenche segundo a cláusula when
data_feriado = data_feriado.withColumn("0-1", \
                                       when(data_feriado.Tipo == 'Útil', '1')\
                                       .when(data_feriado.Tipo != 'Útil', '0'))

display(data_feriado)

Data Dia da Semana Feriado Numero Tipo 0-1 2016-06-30T00:00:00.000+0000 null null 4 Útil 1 2016-07-01T00:00:00.000+0000 null null 5 Útil 1 2016-07-02T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-07-03T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-07-04T00:00:00.000+0000 null null 1 Útil 1 2016-07-05T00:00:00.000+0000 null null 2 Útil 1 2016-07-06T00:00:00.000+0000 null null 3 Útil 1 2016-07-07T00:00:00.000+0000 null null 4 Útil 1 2016-07-08T00:00:00.000+0000 null null 5 Útil 1 2016-07-09T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-07-10T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-07-11T00:00:00.000+0000 null null 1 Útil 1 2016-07-12T00:00:00.000+0000 null null 2 Útil 1 2016-07-13T00:00:00.000+0000 null null 3 Útil 1 2016-07-14T00:00:00.000+0000 null null 4 Útil 1 2016-07-15T00:00:00.000+0000 null null 5 Útil 1 2016-07-16T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-07-17T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-07-18T00:00:00.000+0000 null null 1 Útil 1 2016-07-19T00:00:00.000+0000 null null 2 Útil 1 2016-07-20T00:00:00.000+0000 null null 3 Útil 1 2016-07-21T00:00:00.000+0000 null null 4 Útil 1 2016-07-22T00:00:00.000+0000 null null 5 Útil 1 2016-07-23T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-07-24T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-07-25T00:00:00.000+0000 null null 1 Útil 1 2016-07-26T00:00:00.000+0000 null null 2 Útil 1 2016-07-27T00:00:00.000+0000 null null 3 Útil 1 2016-07-28T00:00:00.000+0000 null null 4 Útil 1 2016-07-29T00:00:00.000+0000 null null 5 Útil 1 2016-07-30T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-07-31T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-08-01T00:00:00.000+0000 null null 1 Útil 1 2016-08-02T00:00:00.000+0000 null null 2 Útil 1 2016-08-03T00:00:00.000+0000 null null 3 Útil 1 2016-08-04T00:00:00.000+0000 null null 4 Útil 1 2016-08-05T00:00:00.000+0000 null null 5 Útil 1 2016-08-06T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-08-07T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-08-08T00:00:00.000+0000 null null 1 Útil 1 2016-08-09T00:00:00.000+0000 null null 2 Útil 1 2016-08-10T00:00:00.000+0000 null null 3 Útil 1 2016-08-11T00:00:00.000+0000 null null 4 Útil 1 2016-08-12T00:00:00.000+0000 null null 5 Útil 1 2016-08-13T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-08-14T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-08-15T00:00:00.000+0000 null null 1 Útil 1 2016-08-16T00:00:00.000+0000 null null 2 Útil 1 2016-08-17T00:00:00.000+0000 null null 3 Útil 1 2016-08-18T00:00:00.000+0000 null null 4 Útil 1 2016-08-19T00:00:00.000+0000 null null 5 Útil 1 2016-08-20T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-08-21T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-08-22T00:00:00.000+0000 null null 1 Útil 1 2016-08-23T00:00:00.000+0000 null null 2 Útil 1 2016-08-24T00:00:00.000+0000 null null 3 Útil 1 2016-08-25T00:00:00.000+0000 null null 4 Útil 1 2016-08-26T00:00:00.000+0000 null null 5 Útil 1 2016-08-27T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-08-28T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-08-29T00:00:00.000+0000 null null 1 Útil 1 2016-08-30T00:00:00.000+0000 null null 2 Útil 1 2016-08-31T00:00:00.000+0000 null null 3 Útil 1 2016-09-01T00:00:00.000+0000 null null 4 Útil 1 2016-09-02T00:00:00.000+0000 null null 5 Útil 1 2016-09-03T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-09-04T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-09-05T00:00:00.000+0000 null null 1 Útil 1 2016-09-06T00:00:00.000+0000 null null 2 Útil 1 2016-09-07T00:00:00.000+0000 quarta-feira Independência do Brasil 3 Independência do Brasil 0 2016-09-08T00:00:00.000+0000 null null 4 Útil 1 2016-09-09T00:00:00.000+0000 null null 5 Útil 1 2016-09-10T00:00:00.000+0000 null null 6 Fim de Semana 0 2016-09-11T00:00:00.000+0000 null null 7 Fim de Semana 0 2016-09-12T00:00:00.000+0000 null null 1 Útil 1 2016-09-13T00:00:00.000+0000 null null 2 Útil 1 2016-09-14T00:00:00.000+0000 null null 3 Útil 1 2016-09-15T00:00:

In [0]:
#Formata a data
data_feriado = data_feriado.withColumn("Data", f.to_date(f.to_timestamp(col("Data"), "dd/MM/yyyy")))
display(data_feriado)

Data Dia da Semana Feriado Numero Tipo 0-1 2016-06-30 null null 4 Útil 1 2016-07-01 null null 5 Útil 1 2016-07-02 null null 6 Fim de Semana 0 2016-07-03 null null 7 Fim de Semana 0 2016-07-04 null null 1 Útil 1 2016-07-05 null null 2 Útil 1 2016-07-06 null null 3 Útil 1 2016-07-07 null null 4 Útil 1 2016-07-08 null null 5 Útil 1 2016-07-09 null null 6 Fim de Semana 0 2016-07-10 null null 7 Fim de Semana 0 2016-07-11 null null 1 Útil 1 2016-07-12 null null 2 Útil 1 2016-07-13 null null 3 Útil 1 2016-07-14 null null 4 Útil 1 2016-07-15 null null 5 Útil 1 2016-07-16 null null 6 Fim de Semana 0 2016-07-17 null null 7 Fim de Semana 0 2016-07-18 null null 1 Útil 1 2016-07-19 null null 2 Útil 1 2016-07-20 null null 3 Útil 1 2016-07-21 null null 4 Útil 1 2016-07-22 null null 5 Útil 1 2016-07-23 null null 6 Fim de Semana 0 2016-07-24 null null 7 Fim de Semana 0 2016-07-25 null null 1 Útil 1 2016-07-26 null null 2 Útil 1 2016-07-27 null null 3 Útil 1 2016-07-28 null null 4 Útil 1 2016-07-29 null null 5 Útil 1 2016-07-30 null null 6 Fim de Semana 0 2016-07-31 null null 7 Fim de Semana 0 2016-08-01 null null 1 Útil 1 2016-08-02 null null 2 Útil 1 2016-08-03 null null 3 Útil 1 2016-08-04 null null 4 Útil 1 2016-08-05 null null 5 Útil 1 2016-08-06 null null 6 Fim de Semana 0 2016-08-07 null null 7 Fim de Semana 0 2016-08-08 null null 1 Útil 1 2016-08-09 null null 2 Útil 1 2016-08-10 null null 3 Útil 1 2016-08-11 null null 4 Útil 1 2016-08-12 null null 5 Útil 1 2016-08-13 null null 6 Fim de Semana 0 2016-08-14 null null 7 Fim de Semana 0 2016-08-15 null null 1 Útil 1 2016-08-16 null null 2 Útil 1 2016-08-17 null null 3 Útil 1 2016-08-18 null null 4 Útil 1 2016-08-19 null null 5 Útil 1 2016-08-20 null null 6 Fim de Semana 0 2016-08-21 null null 7 Fim de Semana 0 2016-08-22 null null 1 Útil 1 2016-08-23 null null 2 Útil 1 2016-08-24 null null 3 Útil 1 2016-08-25 null null 4 Útil 1 2016-08-26 null null 5 Útil 1 2016-08-27 null null 6 Fim de Semana 0 2016-08-28 null null 7 Fim de Semana 0 2016-08-29 null null 1 Útil 1 2016-08-30 null null 2 Útil 1 2016-08-31 null null 3 Útil 1 2016-09-01 null null 4 Útil 1 2016-09-02 null null 5 Útil 1 2016-09-03 null null 6 Fim de Semana 0 2016-09-04 null null 7 Fim de Semana 0 2016-09-05 null null 1 Útil 1 2016-09-06 null null 2 Útil 1 2016-09-07 quarta-feira Independência do Brasil 3 Independência do Brasil 0 2016-09-08 null null 4 Útil 1 2016-09-09 null null 5 Útil 1 2016-09-10 null null 6 Fim de Semana 0 2016-09-11 null null 7 Fim de Semana 0 2016-09-12 null null 1 Útil 1 2016-09-13 null null 2 Útil 1 2016-09-14 null null 3 Útil 1 2016-09-15 null null 4 Útil 1 2016-09-16 null null 5 Útil 1 2016-09-17 null null 6 Fim de Semana 0 2016-09-18 null null 7 Fim de Semana 0 2016-09-19 null null 1 Útil 1 2016-09-20 null null 2 Útil 1 2016-09-21 null null 3 Útil 1 2016-09-22 null null 4 Útil 1 2016-09-23 null null 5 Útil 1 2016-09-24 null null 6 Fim de Semana 0 2016-09-25 null null 7 Fim de Semana 0 2016-09-26 null null 1 Útil 1 2016-09-27 null null 2 Útil 1 2016-09-28 null null 3 Útil 1 2016-09-29 null null 4 Útil 1 2016-09-30 null null 5 Útil 1 2016-10-01 null null 6 Fim de Semana 0 2016-10-02 null null 7 Fim de Semana 0 2016-10-03 null null 1 Útil 1 2016-10-04 null null 2 Útil 1 2016-10-05 null null 3 Útil 1 2016-10-06 null null 4 Útil 1 2016-10-07 null null 5 Útil 1 2016-10-08 null null 6 Fim de Semana 0 2016-10-09 null null 7 Fim de Semana 0 2016-10-10 null null 1 Útil 1 2016-10-11 null null 2 Útil 1 2016-10-12 quarta-feira Nossa Sr.a Aparecida - Padroeira do Brasil 3 Nossa Sr.a Aparecida - Padroeira do Brasil 0 2016-10-13 null null 4 Útil 1 2016-10-14 null null 5 Útil 1 2016-10-15 null null 6 Fim de Semana 0 2016-10-16 null null 7 Fim de Semana 0 2016-10-17 null null 1 Útil 1 2016-10-18 null null 2 Útil 1 2016-10-19 null null 3 Útil 1 2016-10-20 null null 4 Útil 1 2016-10-21 null null 5 Útil 1 2016-10-22 null null 6 Fim de Semana 0 2016-10-23 null null 7 Fim de Semana 0 2016-10-24 null null 1 Útil 1 2016-10-25 

In [0]:
#Drop coluna "Dia da Semana" e "Feriado"
data_feriado = data_feriado.drop("Dia da Semana")
data_feriado = data_feriado.drop("Feriado")

display(data_feriado)

Data Numero Tipo 0-1 2016-06-30 4 Útil 1 2016-07-01 5 Útil 1 2016-07-02 6 Fim de Semana 0 2016-07-03 7 Fim de Semana 0 2016-07-04 1 Útil 1 2016-07-05 2 Útil 1 2016-07-06 3 Útil 1 2016-07-07 4 Útil 1 2016-07-08 5 Útil 1 2016-07-09 6 Fim de Semana 0 2016-07-10 7 Fim de Semana 0 2016-07-11 1 Útil 1 2016-07-12 2 Útil 1 2016-07-13 3 Útil 1 2016-07-14 4 Útil 1 2016-07-15 5 Útil 1 2016-07-16 6 Fim de Semana 0 2016-07-17 7 Fim de Semana 0 2016-07-18 1 Útil 1 2016-07-19 2 Útil 1 2016-07-20 3 Útil 1 2016-07-21 4 Útil 1 2016-07-22 5 Útil 1 2016-07-23 6 Fim de Semana 0 2016-07-24 7 Fim de Semana 0 2016-07-25 1 Útil 1 2016-07-26 2 Útil 1 2016-07-27 3 Útil 1 2016-07-28 4 Útil 1 2016-07-29 5 Útil 1 2016-07-30 6 Fim de Semana 0 2016-07-31 7 Fim de Semana 0 2016-08-01 1 Útil 1 2016-08-02 2 Útil 1 2016-08-03 3 Útil 1 2016-08-04 4 Útil 1 2016-08-05 5 Útil 1 2016-08-06 6 Fim de Semana 0 2016-08-07 7 Fim de Semana 0 2016-08-08 1 Útil 1 2016-08-09 2 Útil 1 2016-08-10 3 Útil 1 2016-08-11 4 Útil 1 2016-08-12 5 Útil 1 2016-08-13 6 Fim de Semana 0 2016-08-14 7 Fim de Semana 0 2016-08-15 1 Útil 1 2016-08-16 2 Útil 1 2016-08-17 3 Útil 1 2016-08-18 4 Útil 1 2016-08-19 5 Útil 1 2016-08-20 6 Fim de Semana 0 2016-08-21 7 Fim de Semana 0 2016-08-22 1 Útil 1 2016-08-23 2 Útil 1 2016-08-24 3 Útil 1 2016-08-25 4 Útil 1 2016-08-26 5 Útil 1 2016-08-27 6 Fim de Semana 0 2016-08-28 7 Fim de Semana 0 2016-08-29 1 Útil 1 2016-08-30 2 Útil 1 2016-08-31 3 Útil 1 2016-09-01 4 Útil 1 2016-09-02 5 Útil 1 2016-09-03 6 Fim de Semana 0 2016-09-04 7 Fim de Semana 0 2016-09-05 1 Útil 1 2016-09-06 2 Útil 1 2016-09-07 3 Independência do Brasil 0 2016-09-08 4 Útil 1 2016-09-09 5 Útil 1 2016-09-10 6 Fim de Semana 0 2016-09-11 7 Fim de Semana 0 2016-09-12 1 Útil 1 2016-09-13 2 Útil 1 2016-09-14 3 Útil 1 2016-09-15 4 Útil 1 2016-09-16 5 Útil 1 2016-09-17 6 Fim de Semana 0 2016-09-18 7 Fim de Semana 0 2016-09-19 1 Útil 1 2016-09-20 2 Útil 1 2016-09-21 3 Útil 1 2016-09-22 4 Útil 1 2016-09-23 5 Útil 1 2016-09-24 6 Fim de Semana 0 2016-09-25 7 Fim de Semana 0 2016-09-26 1 Útil 1 2016-09-27 2 Útil 1 2016-09-28 3 Útil 1 2016-09-29 4 Útil 1 2016-09-30 5 Útil 1 2016-10-01 6 Fim de Semana 0 2016-10-02 7 Fim de Semana 0 2016-10-03 1 Útil 1 2016-10-04 2 Útil 1 2016-10-05 3 Útil 1 2016-10-06 4 Útil 1 2016-10-07 5 Útil 1 2016-10-08 6 Fim de Semana 0 2016-10-09 7 Fim de Semana 0 2016-10-10 1 Útil 1 2016-10-11 2 Útil 1 2016-10-12 3 Nossa Sr.a Aparecida - Padroeira do Brasil 0 2016-10-13 4 Útil 1 2016-10-14 5 Útil 1 2016-10-15 6 Fim de Semana 0 2016-10-16 7 Fim de Semana 0 2016-10-17 1 Útil 1 2016-10-18 2 Útil 1 2016-10-19 3 Útil 1 2016-10-20 4 Útil 1 2016-10-21 5 Útil 1 2016-10-22 6 Fim de Semana 0 2016-10-23 7 Fim de Semana 0 2016-10-24 1 Útil 1 2016-10-25 2 Útil 1 2016-10-26 3 Útil 1 2016-10-27 4 Útil 1 2016-10-28 5 Útil 1 2016-10-29 6 Fim de Semana 0 2016-10-30 7 Fim de Semana 0 2016-10-31 1 Útil 1 2016-11-01 2 Útil 1 2016-11-02 3 Finados 0 2016-11-03 4 Útil 1 2016-11-04 5 Útil 1 2016-11-05 6 Fim de Semana 0 2016-11-06 7 Fim de Semana 0 2016-11-07 1 Útil 1 2016-11-08 2 Útil 1 2016-11-09 3 Útil 1 2016-11-10 4 Útil 1 2016-11-11 5 Útil 1 2016-11-12 6 Fim de Semana 0 2016-11-13 7 Fim de Semana 0 2016-11-14 1 Útil 1 2016-11-15 2 Proclamação da República 0 2016-11-16 3 Útil 1 2016-11-17 4 Útil 1 2016-11-18 5 Útil 1 2016-11-19 6 Fim de Semana 0 2016-11-20 7 Fim de Semana 0 2016-11-21 1 Útil 1 2016-11-22 2 Útil 1 2016-11-23 3 Útil 1 2016-11-24 4 Útil 1 2016-11-25 5 Útil 1 2016-11-26 6 Fim de Semana 0 2016-11-27 7 Fim de Semana 0 2016-11-28 1 Útil 1 2016-11-29 2 Útil 1 2016-11-30 3 Útil 1 2016-12-01 4 Útil 1 2016-12-02 5 Útil 1 2016-12-03 6 Fim de Semana 0 2016-12-04 7 Fim de Semana 0 2016-12-05 1 Útil 1 2016-12-06 2 Útil 1 2016-12-07 3 Útil 1 2016-12-08 4 Útil 1 2016-12-09 5 Útil 1 2016-12-10 6 Fim de Semana 0 2016-12-11 7 Fim de Semana 0 2016-12-12 1 Útil 1 2016-12-13 2 Útil 1 2016-12-14 3 Útil 1 2016-12-15 4 Útil 1 2016-12-16 5 Útil 1 2016-12-17 6 Fim de Semana 0 2016-12-18 7 Fim de Semana 0 2016-12-1

In [0]:
#tipagem de dados

data_feriado = data_feriado.withColumn("Numero", col("Numero").cast("int")).withColumn("0-1", col("0-1").cast("int"))

display(data_feriado)

Data Numero Tipo 0-1 2016-06-30 4 Útil 1 2016-07-01 5 Útil 1 2016-07-02 6 Fim de Semana 0 2016-07-03 7 Fim de Semana 0 2016-07-04 1 Útil 1 2016-07-05 2 Útil 1 2016-07-06 3 Útil 1 2016-07-07 4 Útil 1 2016-07-08 5 Útil 1 2016-07-09 6 Fim de Semana 0 2016-07-10 7 Fim de Semana 0 2016-07-11 1 Útil 1 2016-07-12 2 Útil 1 2016-07-13 3 Útil 1 2016-07-14 4 Útil 1 2016-07-15 5 Útil 1 2016-07-16 6 Fim de Semana 0 2016-07-17 7 Fim de Semana 0 2016-07-18 1 Útil 1 2016-07-19 2 Útil 1 2016-07-20 3 Útil 1 2016-07-21 4 Útil 1 2016-07-22 5 Útil 1 2016-07-23 6 Fim de Semana 0 2016-07-24 7 Fim de Semana 0 2016-07-25 1 Útil 1 2016-07-26 2 Útil 1 2016-07-27 3 Útil 1 2016-07-28 4 Útil 1 2016-07-29 5 Útil 1 2016-07-30 6 Fim de Semana 0 2016-07-31 7 Fim de Semana 0 2016-08-01 1 Útil 1 2016-08-02 2 Útil 1 2016-08-03 3 Útil 1 2016-08-04 4 Útil 1 2016-08-05 5 Útil 1 2016-08-06 6 Fim de Semana 0 2016-08-07 7 Fim de Semana 0 2016-08-08 1 Útil 1 2016-08-09 2 Útil 1 2016-08-10 3 Útil 1 2016-08-11 4 Útil 1 2016-08-12 5 Útil 1 2016-08-13 6 Fim de Semana 0 2016-08-14 7 Fim de Semana 0 2016-08-15 1 Útil 1 2016-08-16 2 Útil 1 2016-08-17 3 Útil 1 2016-08-18 4 Útil 1 2016-08-19 5 Útil 1 2016-08-20 6 Fim de Semana 0 2016-08-21 7 Fim de Semana 0 2016-08-22 1 Útil 1 2016-08-23 2 Útil 1 2016-08-24 3 Útil 1 2016-08-25 4 Útil 1 2016-08-26 5 Útil 1 2016-08-27 6 Fim de Semana 0 2016-08-28 7 Fim de Semana 0 2016-08-29 1 Útil 1 2016-08-30 2 Útil 1 2016-08-31 3 Útil 1 2016-09-01 4 Útil 1 2016-09-02 5 Útil 1 2016-09-03 6 Fim de Semana 0 2016-09-04 7 Fim de Semana 0 2016-09-05 1 Útil 1 2016-09-06 2 Útil 1 2016-09-07 3 Independência do Brasil 0 2016-09-08 4 Útil 1 2016-09-09 5 Útil 1 2016-09-10 6 Fim de Semana 0 2016-09-11 7 Fim de Semana 0 2016-09-12 1 Útil 1 2016-09-13 2 Útil 1 2016-09-14 3 Útil 1 2016-09-15 4 Útil 1 2016-09-16 5 Útil 1 2016-09-17 6 Fim de Semana 0 2016-09-18 7 Fim de Semana 0 2016-09-19 1 Útil 1 2016-09-20 2 Útil 1 2016-09-21 3 Útil 1 2016-09-22 4 Útil 1 2016-09-23 5 Útil 1 2016-09-24 6 Fim de Semana 0 2016-09-25 7 Fim de Semana 0 2016-09-26 1 Útil 1 2016-09-27 2 Útil 1 2016-09-28 3 Útil 1 2016-09-29 4 Útil 1 2016-09-30 5 Útil 1 2016-10-01 6 Fim de Semana 0 2016-10-02 7 Fim de Semana 0 2016-10-03 1 Útil 1 2016-10-04 2 Útil 1 2016-10-05 3 Útil 1 2016-10-06 4 Útil 1 2016-10-07 5 Útil 1 2016-10-08 6 Fim de Semana 0 2016-10-09 7 Fim de Semana 0 2016-10-10 1 Útil 1 2016-10-11 2 Útil 1 2016-10-12 3 Nossa Sr.a Aparecida - Padroeira do Brasil 0 2016-10-13 4 Útil 1 2016-10-14 5 Útil 1 2016-10-15 6 Fim de Semana 0 2016-10-16 7 Fim de Semana 0 2016-10-17 1 Útil 1 2016-10-18 2 Útil 1 2016-10-19 3 Útil 1 2016-10-20 4 Útil 1 2016-10-21 5 Útil 1 2016-10-22 6 Fim de Semana 0 2016-10-23 7 Fim de Semana 0 2016-10-24 1 Útil 1 2016-10-25 2 Útil 1 2016-10-26 3 Útil 1 2016-10-27 4 Útil 1 2016-10-28 5 Útil 1 2016-10-29 6 Fim de Semana 0 2016-10-30 7 Fim de Semana 0 2016-10-31 1 Útil 1 2016-11-01 2 Útil 1 2016-11-02 3 Finados 0 2016-11-03 4 Útil 1 2016-11-04 5 Útil 1 2016-11-05 6 Fim de Semana 0 2016-11-06 7 Fim de Semana 0 2016-11-07 1 Útil 1 2016-11-08 2 Útil 1 2016-11-09 3 Útil 1 2016-11-10 4 Útil 1 2016-11-11 5 Útil 1 2016-11-12 6 Fim de Semana 0 2016-11-13 7 Fim de Semana 0 2016-11-14 1 Útil 1 2016-11-15 2 Proclamação da República 0 2016-11-16 3 Útil 1 2016-11-17 4 Útil 1 2016-11-18 5 Útil 1 2016-11-19 6 Fim de Semana 0 2016-11-20 7 Fim de Semana 0 2016-11-21 1 Útil 1 2016-11-22 2 Útil 1 2016-11-23 3 Útil 1 2016-11-24 4 Útil 1 2016-11-25 5 Útil 1 2016-11-26 6 Fim de Semana 0 2016-11-27 7 Fim de Semana 0 2016-11-28 1 Útil 1 2016-11-29 2 Útil 1 2016-11-30 3 Útil 1 2016-12-01 4 Útil 1 2016-12-02 5 Útil 1 2016-12-03 6 Fim de Semana 0 2016-12-04 7 Fim de Semana 0 2016-12-05 1 Útil 1 2016-12-06 2 Útil 1 2016-12-07 3 Útil 1 2016-12-08 4 Útil 1 2016-12-09 5 Útil 1 2016-12-10 6 Fim de Semana 0 2016-12-11 7 Fim de Semana 0 2016-12-12 1 Útil 1 2016-12-13 2 Útil 1 2016-12-14 3 Útil 1 2016-12-15 4 Útil 1 2016-12-16 5 Útil 1 2016-12-17 6 Fim de Semana 0 2016-12-18 7 Fim de Semana 0 2016-12-1

#**Vendas**
Neste bloco, foram fornecidos 2 CSVs (um com os dados mensais e outro com os dados semanais) contendo as vendas para o consumidor final, tendo o vin como código do carro vendido
Tendo como objetivo descobrir quantas vendas foram realizadas desde o começo do ano até a data mais recente.
Estes dados são muito importantes pois com eles poderiam ser feitas muitas consultas, como por exemplo:
* Qual foi a marca que vendeu mais;
* Qual modelo vendeu mais;
* Qual o mês em que houveram mais vendas;
* Ou tambem, pelo contrário, qual modelo, marca ou mês em que se vendeu menos para que decisões possam ser tomadas a respeito.

In [0]:
#Leitura CSVs vendas
dados_mensais = spark.read.options(sep=";", header=True, encoding = "UTF-8")\
    .csv("/mnt/blobed/modulo_02/detran/mensal/2022_09_06_detranmensal.csv")
dados_semanais = spark.read.options(sep=";", header=True, encoding = "UTF-8")\
    .csv("/mnt/blobed/modulo_02/detran/semanal/2022_09_05_detransemanal.csv")

display(dados_semanais)
display(dados_mensais)

mes marca modelo versao dia ano vin 9 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 1 2022 9BG148FK0PC408873 9 CHEVROLET N400 MAX N400 MAX 1.5 1 2022 LZWCDAGA5PC801017 9 VOLKSWAGEN GOL GOL HB 1.6 1 2022 9BWAB45U7NT120908 9 VOLKSWAGEN GOL GOL HB 1.6 1 2022 9BWAB45U5NT122446 9 CHEVROLET GROOVE GROOVE 1.5 1 2022 LZWADAGA5PG003665 9 VOLKSWAGEN T-CROSS T CROSS TSI 1.0 AUT 1 2022 9BWBH6BF7N4066511 9 CHEVROLET N400 MAX N400 MAX 1.5 1 2022 LZWCDAGA9PC803787 9 CHEVROLET N400 MAX N400 MAX 1.5 1 2022 LZWCDAGA1PC803802 9 CHEVROLET N400 MAX N400 MAX 1.5 1 2022 LZWCDAGA1PC802231 9 VOLKSWAGEN SAVEIRO SAVEIRO CS 1.6 1 2022 9BWKL45UXNP046264 9 TOYOTA HILUX HILUX 4X2 2.4 MT SR 1 2022 8AJJB3DD1P4237160 9 VOLKSWAGEN GOL GOL HB 1.6 1 2022 9BWAB45U2NT122386 9 VOLKSWAGEN GOL GOL HB 1.6 1 2022 9BWAB45U7NT122948 9 HYUNDAI HD 35 HD35 SWB 2P 2.5 1 2022 KMFVA17RPPC360549 9 HYUNDAI HD 35 HD35 SWB 2P 2.5 1 2022 KMFVA17RPPC360548 9 VOLKSWAGEN VOYAGE VOYAGE 1.6 1 2022 9BWDB45U9NT127906 9 HYUNDAI HD 35 HD 35 LWB 2.5 1 2022 KMFVA17RPNC360146 9 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 1 2022 MALB241CAPM119904 9 BMW X6 X6 M50I 4X4 4.4 AUT 1 2022 WBACY8103N9L11585 9 TOYOTA HILUX NEW HILUX 4X4 2.4L MT DX 1 2022 8AJDB3C5P1325144 9 CHEVROLET TRACKER TRACKER 1.2T LS MT P 1 2022 9BGEA76C0PB135857 9 PEUGEOT 2008 2008 PURETECH 130 1.2 1 2022 VR3USHNSKPJ513630 9 VOLKSWAGEN POLO POLO HATCH BACK 1.6 AT 1 2022 9BWAL5BZ8NP039783 9 TOYOTA YARIS YARIS SEDAN XLI 1.5 TM 1 2022 MR2B29F37N1249172 9 TOYOTA RAV4 RAV4 LE 2.0 4X2 CVT 1 2022 JTMZ43FV0PD133196 9 TOYOTA RAV4 RAV4 LE 2.0 4X2 MT 1 2022 JTMZ43FV9PD132421 9 TOYOTA YARIS YARIS SEDAN GLI 1.5 MT 1 2022 MR2B29F38N1242070 9 TOYOTA COROLLA CROSS COROLLA CROSS SEG 2.0 1 2022 9BRK4AAG5P0057859 9 VOLKSWAGEN GOL GOL HB 1.6 1 2022 9BWAB45U8NT091368 9 TOYOTA HILUX HILUX 4X2 2.4 MT DX 2 2022 8AJCB3DD7N3911372 9 VOLKSWAGEN TOUAREG TOUAREG 4X4 3.0 AT 2 2022 WVGZZZCRZND021792 9 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 1 2022 8AJKB3CD6N1641785 9 FORD TERRITORY TERRITORY 1.5 AUT 1 2022 LJXCU2BB6NTF15753 9 FORD TERRITORY TERRITORY 1.5 AUT 1 2022 LJXCU2BB6NTF15767 9 CHEVROLET N400 MAX N400 MAX 1.5 1 2022 LZWCDAGA0PC802415 9 TOYOTA HILUX HILUX 4X4 2.4 DX MT 2 2022 8AJDB3CD1P1326596 9 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 1 2022 9BG148FK0PC408966 9 HYUNDAI NEW CRETA CRETA 1.5 1 2022 MALPB812APM309405 9 VOLKSWAGEN CONSTELLATION CONSTELLATION 17.280 2 2022 953658246NR029219 9 CHEVROLET ONIX ONIX HB RS 1.OT 1 2022 9BGED48K0PG160330 9 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 1 2022 8AJDB3CD9P1326670 9 CHEVROLET ONIX ONIX HB RS 1.OT 1 2022 9BGED48K0PG156990 9 CHEVROLET TRACKER TRACKER 1.2T AUT 1 2022 9BGEN76C0PB123591 9 CHEVROLET GROOVE GROOVE PREMIER 1.5 1 2022 LZWADAGA0NG021925 9 RENAULT DUSTER DUSTER 4X2 1.6 2 2022 VF1HJD208PA253252 9 TOYOTA YARIS YARIS SEDAN OTTO 1.5 1 2022 MR2B29F3XN1251207 9 CHEVROLET NPR NPR 816 VL20 1 2022 JAANPR75KP7100218 9 RENAULT DUSTER DUSTER 4X2 1.6 1 2022 VF1HJD206PA260023 9 TOYOTA YARIS YARIS HB OTTO 1.5 1 2022 MR2K29F35N1249820 9 TOYOTA RAV4 RAV4 4X4 OTTO 2.0 2 2022 JTMB43FV8PD035874 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA3PC803879 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA4PC800943 9 HYUNDAI VENUE VENUE QX 1.6 MT VALUE 1 2022 KMHRC812APU192146 9 TOYOTA RAIZE RAIZE CVT 1.2 AUT 2 2022 MHKAB1BA4NJ017854 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA6PC801995 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA2PC803856 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA4PC803860 9 HYUNDAI GRAND I-10 GRAND I10 HB 1.2 1 2022 MALB251CAPM324452 9 CHEVROLET N400 MAX N400 MAX 1.5 1 2022 LZWCDAGA4PC803826 9 VOLKSWAGEN POLO POLO HATCH BACK 1.6 AT 2 2022 9BWAL5BZ1NP040578 9 PEUGEOT 3008 3008 PURETECH 180 EAT8 1.6 AUT 2 2022 VF3M45GFUPS006157 9 FORD TERRITORY NEW TERRITORY TITANIUM 1.5L GTDI AT 2 2022 LJXCU2BB4NTF12138 9 FORD TERRITORY NEW TERRITORY TREND 1.5L GTDI AT 2 2022 LJXCU2BB7NTF15910 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG3N0053998 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9B

mes marca modelo versao dia ano vin 1 PEUGEOT 2008 2008 BLUE HDI 130 EAT8 1.5 AUT 6 2022 VR3UDYHZSNJ526248 1 CHEVROLET SAIL SAIL 1.5 6 2022 LSGHD52H3ND024627 1 PEUGEOT PARTNER PARTNER 1.6 4 2022 VR3EF9HPANJ531887 1 CHEVROLET CAPTIVA CAPTIVA 1.5 AUT 24 2022 LZWADAGA7NB024303 1 CHEVROLET N400 MAX N400 MAX 1.5 3 2022 LZWCDAGA3NC807556 1 FORD NEW RANGER RANGER RAPTOR 2.0 6 2022 MPBUR2366NX359311 1 CHEVROLET GROOVE GROOVE LTZ 1.5 3 2022 LZWADAGA8NG006685 1 CHEVROLET GROOVE GROOVE LTZ 1.5 3 2022 LZWADAGA2NG005841 1 CHEVROLET GROOVE GROOVE LTZ 1.5 3 2022 LZWADAGA7NG006144 1 CHEVROLET GROOVE GROOVE PREMIER 1.5 3 2022 LZWADAGA1NG007063 1 PEUGEOT 2008 2008 PURETECH 130 EAT8 1.2 AUT 3 2022 VR3USHNSSNJ525794 1 CHEVROLET CAPTIVA CAPTIVA MT6 4X2 1.5 24 2022 LZWADAGA6NB027919 1 CHEVROLET CAPTIVA CAPTIVA MT6 1.5 13 2022 LZWADAGAXNB027826 1 PEUGEOT 208 208 PURETECH 75 1.2 4 2022 VR3UPHMGBNT002023 1 PEUGEOT 208 208 PURETECH 75 1.2 6 2022 VR3UPHMGBNT001380 1 HYUNDAI ATOS AH2 ATOS 1.1 6 2022 MALAF51CANM163805 1 HYUNDAI ACCENT HCI ACCENT HCI 1.4 6 2022 MALC741BAMM296216 1 CHEVROLET N400 MAX N400 MAX 1.5 3 2022 LZWCDAGA5NC807509 1 PEUGEOT 2008 2008 PURETECH 130 EAT8 1.2 AUT 4 2022 VR3USHNSSNJ526477 1 VOLKSWAGEN VOYAGE VOYAGE 1.6 14 2022 9BWDB45U1NT092231 1 TOYOTA HILUX HILUX DOBLE CABINA 2.4 6 2022 8AJJB3DD0N4234313 1 FORD TERRITORY TERRITORY TREND 1.5 AT 6 2022 LJXCU2BB5NTF05652 1 PEUGEOT 3008 3008 BLUE HDI 130 EAT8 1.5 AUT 6 2022 VF3MCYHZUNS007139 1 FORD F-150 F150 LARIAT LUXURY 4X4 3.0 3 2022 1FTFW1E10MFC13923 1 PEUGEOT 2008 2008 ALLURE BLUEHDI 1.5 AUT 14 2022 VR3UDYHZSNJ533951 1 TOYOTA HILUX HILUX DOBLE CABINA 2.4 6 2022 8AJCB3DD9N3909266 1 TOYOTA RAV4 RAV4 OTTO 2.0 6 2022 JTMZ43FV9ND104731 1 TOYOTA FORTUNER FORTUNER SRV 2.7 AUT 6 2022 8AJCX3GS8N0130793 1 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 6 2022 8AJKB3CD3N1635359 1 TOYOTA YARIS YARIS SEDAN GLI 1.5 3 2022 MR2B29F32N1235728 1 TOYOTA YARIS YARIS SEDAN XLI 1.5 3 2022 MR2B29F33N1236600 1 TOYOTA HILUX HILUX DOBLE CABINA 2.4 24 2022 8AJCB3DDXN3909387 1 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 24 2022 8AJDB3CD8N1318234 1 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 1.2 3 2022 MALB241CANM091872 1 CHEVROLET ONIX ONIX HB RS 1.OT 13 2022 9BGEN48K0NG135804 1 PEUGEOT 5008 5008 ALLURE 1.5 AUT 6 2022 VF3MCYHZUNL001187 1 RENAULT OROCH OROCH 2.0 4 2022 93Y9SR5A6NJ126126 1 PEUGEOT 2008 2008 PURETECH 130 1.2 6 2022 VR3USHNSKNJ526158 1 PEUGEOT 208 208 BLUE HDI 100 4X2 1.5 6 2022 VR3UBYHTKNT002161 1 HYUNDAI VERNA VERNA CB 1.4 3 2022 LBECBACB2NW163888 1 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 6 2022 MALB251CANM236453 1 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 6 2022 MALB251CANM236460 1 TOYOTA HILUX HI LUX 2.4 14 2022 8AJJB3DDXN4234822 1 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 3 2022 MALB251CANM235825 1 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MT PLUS 24 2022 MALB251CANM236448 1 PEUGEOT 301 301 HDI 92HP 1.6 6 2022 VF3DD9HP0NJ524448 1 CHEVROLET SILVERADO SILVERADO DCAB 4X4 5.3 AT 7 2022 3GCPY9ED1MG463502 1 CHEVROLET TRACKER TRACKER 1.2T AUT 14 2022 9BGEN76C0NB143586 1 PEUGEOT PARTNER PARTNER HDI 92 L1 1.6 7 2022 VR3EF9HPANJ530938 1 PEUGEOT PARTNER PARTNER HDI 92 L1 1.6 7 2022 VR3EF9HPANJ530936 1 PEUGEOT PARTNER PARTNER HDI 92 L2 1.6 7 2022 VR3EF9HPANJ528709 1 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 4 2022 8AJKB3CD9N1635785 1 CHEVROLET SILVERADO SILVERADO CC DCAB 4X4 5.3 AUT 7 2022 3GCPY9ED9MG460654 1 CHEVROLET TRACKER TRACKER 1.2T AUT 24 2022 9BGEN76C0NB142181 1 FORD TERRITORY TERRITORY TREND GTDI 1.5 AT 24 2022 LJXCU2BB4NTF07151 1 FORD TERRITORY TERRITORY TREND GTDI 1.5 AT 24 2022 LJXCU2BB5NTF04999 1 HYUNDAI TUCSON NX4 TUCSON NX4 GDI 7DCT 1.6 AUT 13 2022 KMHJB81BGNU101161 1 TOYOTA YARIS GR YARIS TURBO 4X4 1.6 24 2022 JTDAF4E35NA014698 1 PEUGEOT 2008 2008 ACTIVE 1.2 13 2022 VR3USHNSKNJ524322 1 CHEVROLET ONIX ONIX NB LT 1.0T 13 2022 9BGEN69K0NG135735 1 CHEVROLET ONIX ONIX NB PREMIER 1.0T AUT 13 2022 9BGEP69K0NG135874 1 CHEVROLET ONIX ONIX NB LT 1.0T 13 2022 9BGEB69K0NG133591 1 C

In [0]:
#DADOS SEMANAIS
#Cria coluna data
#Edita o nome das outras colunas
dados_semanais_data = dados_semanais.select(\
    concat_ws('-',dados_semanais.ano, dados_semanais.mes, dados_semanais.dia)\
    .alias("Data"), "Marca", "Modelo", "Versao", "Vin", "Mes")

#Converte a nova coluna (Data) no tipo date
dados_semanais_data = dados_semanais_data.withColumn("Data", col("Data").cast("date"))

display(dados_semanais_data)


Data Marca Modelo Versao Vin Mes 2022-09-01 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 9BG148FK0PC408873 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA5PC801017 9 2022-09-01 VOLKSWAGEN GOL GOL HB 1.6 9BWAB45U7NT120908 9 2022-09-01 VOLKSWAGEN GOL GOL HB 1.6 9BWAB45U5NT122446 9 2022-09-01 CHEVROLET GROOVE GROOVE 1.5 LZWADAGA5PG003665 9 2022-09-01 VOLKSWAGEN T-CROSS T CROSS TSI 1.0 AUT 9BWBH6BF7N4066511 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA9PC803787 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA1PC803802 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA1PC802231 9 2022-09-01 VOLKSWAGEN SAVEIRO SAVEIRO CS 1.6 9BWKL45UXNP046264 9 2022-09-01 TOYOTA HILUX HILUX 4X2 2.4 MT SR 8AJJB3DD1P4237160 9 2022-09-01 VOLKSWAGEN GOL GOL HB 1.6 9BWAB45U2NT122386 9 2022-09-01 VOLKSWAGEN GOL GOL HB 1.6 9BWAB45U7NT122948 9 2022-09-01 HYUNDAI HD 35 HD35 SWB 2P 2.5 KMFVA17RPPC360549 9 2022-09-01 HYUNDAI HD 35 HD35 SWB 2P 2.5 KMFVA17RPPC360548 9 2022-09-01 VOLKSWAGEN VOYAGE VOYAGE 1.6 9BWDB45U9NT127906 9 2022-09-01 HYUNDAI HD 35 HD 35 LWB 2.5 KMFVA17RPNC360146 9 2022-09-01 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 MALB241CAPM119904 9 2022-09-01 BMW X6 X6 M50I 4X4 4.4 AUT WBACY8103N9L11585 9 2022-09-01 TOYOTA HILUX NEW HILUX 4X4 2.4L MT DX 8AJDB3C5P1325144 9 2022-09-01 CHEVROLET TRACKER TRACKER 1.2T LS MT P 9BGEA76C0PB135857 9 2022-09-01 PEUGEOT 2008 2008 PURETECH 130 1.2 VR3USHNSKPJ513630 9 2022-09-01 VOLKSWAGEN POLO POLO HATCH BACK 1.6 AT 9BWAL5BZ8NP039783 9 2022-09-01 TOYOTA YARIS YARIS SEDAN XLI 1.5 TM MR2B29F37N1249172 9 2022-09-01 TOYOTA RAV4 RAV4 LE 2.0 4X2 CVT JTMZ43FV0PD133196 9 2022-09-01 TOYOTA RAV4 RAV4 LE 2.0 4X2 MT JTMZ43FV9PD132421 9 2022-09-01 TOYOTA YARIS YARIS SEDAN GLI 1.5 MT MR2B29F38N1242070 9 2022-09-01 TOYOTA COROLLA CROSS COROLLA CROSS SEG 2.0 9BRK4AAG5P0057859 9 2022-09-01 VOLKSWAGEN GOL GOL HB 1.6 9BWAB45U8NT091368 9 2022-09-02 TOYOTA HILUX HILUX 4X2 2.4 MT DX 8AJCB3DD7N3911372 9 2022-09-02 VOLKSWAGEN TOUAREG TOUAREG 4X4 3.0 AT WVGZZZCRZND021792 9 2022-09-01 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJKB3CD6N1641785 9 2022-09-01 FORD TERRITORY TERRITORY 1.5 AUT LJXCU2BB6NTF15753 9 2022-09-01 FORD TERRITORY TERRITORY 1.5 AUT LJXCU2BB6NTF15767 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA0PC802415 9 2022-09-02 TOYOTA HILUX HILUX 4X4 2.4 DX MT 8AJDB3CD1P1326596 9 2022-09-01 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 9BG148FK0PC408966 9 2022-09-01 HYUNDAI NEW CRETA CRETA 1.5 MALPB812APM309405 9 2022-09-02 VOLKSWAGEN CONSTELLATION CONSTELLATION 17.280 953658246NR029219 9 2022-09-01 CHEVROLET ONIX ONIX HB RS 1.OT 9BGED48K0PG160330 9 2022-09-01 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD9P1326670 9 2022-09-01 CHEVROLET ONIX ONIX HB RS 1.OT 9BGED48K0PG156990 9 2022-09-01 CHEVROLET TRACKER TRACKER 1.2T AUT 9BGEN76C0PB123591 9 2022-09-01 CHEVROLET GROOVE GROOVE PREMIER 1.5 LZWADAGA0NG021925 9 2022-09-02 RENAULT DUSTER DUSTER 4X2 1.6 VF1HJD208PA253252 9 2022-09-01 TOYOTA YARIS YARIS SEDAN OTTO 1.5 MR2B29F3XN1251207 9 2022-09-01 CHEVROLET NPR NPR 816 VL20 JAANPR75KP7100218 9 2022-09-01 RENAULT DUSTER DUSTER 4X2 1.6 VF1HJD206PA260023 9 2022-09-01 TOYOTA YARIS YARIS HB OTTO 1.5 MR2K29F35N1249820 9 2022-09-02 TOYOTA RAV4 RAV4 4X4 OTTO 2.0 JTMB43FV8PD035874 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA3PC803879 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA4PC800943 9 2022-09-01 HYUNDAI VENUE VENUE QX 1.6 MT VALUE KMHRC812APU192146 9 2022-09-02 TOYOTA RAIZE RAIZE CVT 1.2 AUT MHKAB1BA4NJ017854 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA6PC801995 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA2PC803856 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA4PC803860 9 2022-09-01 HYUNDAI GRAND I-10 GRAND I10 HB 1.2 MALB251CAPM324452 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA4PC803826 9 2022-09-02 VOLKSWAGEN POLO POLO HATCH BACK 1.6 AT 9BWAL5BZ1NP040578 9 2022-09-02 PEUGEOT 3008 3008 PURETECH 180 EAT8 1.6 AUT VF3M45GFUPS006157 9 2022-09-02 FORD TERRITORY NEW TERRITORY TITA

In [0]:
#DADOS MENSAIS
#Cria coluna data
#Edita o nome das outras colunas
dados_mensais_data = dados_mensais.select(\
    concat_ws('-',dados_mensais.ano, dados_mensais.mes, dados_mensais.dia)\
    .alias("Data"), "Marca", "Modelo", "Versao", "Vin", "Mes")

#Converte a nova coluna (Data) no tipo date
dados_mensais_data = dados_mensais_data.withColumn("Data", col("Data").cast("date"))

display(dados_mensais_data)

Data Marca Modelo Versao Vin Mes 2022-01-06 PEUGEOT 2008 2008 BLUE HDI 130 EAT8 1.5 AUT VR3UDYHZSNJ526248 1 2022-01-06 CHEVROLET SAIL SAIL 1.5 LSGHD52H3ND024627 1 2022-01-04 PEUGEOT PARTNER PARTNER 1.6 VR3EF9HPANJ531887 1 2022-01-24 CHEVROLET CAPTIVA CAPTIVA 1.5 AUT LZWADAGA7NB024303 1 2022-01-03 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA3NC807556 1 2022-01-06 FORD NEW RANGER RANGER RAPTOR 2.0 MPBUR2366NX359311 1 2022-01-03 CHEVROLET GROOVE GROOVE LTZ 1.5 LZWADAGA8NG006685 1 2022-01-03 CHEVROLET GROOVE GROOVE LTZ 1.5 LZWADAGA2NG005841 1 2022-01-03 CHEVROLET GROOVE GROOVE LTZ 1.5 LZWADAGA7NG006144 1 2022-01-03 CHEVROLET GROOVE GROOVE PREMIER 1.5 LZWADAGA1NG007063 1 2022-01-03 PEUGEOT 2008 2008 PURETECH 130 EAT8 1.2 AUT VR3USHNSSNJ525794 1 2022-01-24 CHEVROLET CAPTIVA CAPTIVA MT6 4X2 1.5 LZWADAGA6NB027919 1 2022-01-13 CHEVROLET CAPTIVA CAPTIVA MT6 1.5 LZWADAGAXNB027826 1 2022-01-04 PEUGEOT 208 208 PURETECH 75 1.2 VR3UPHMGBNT002023 1 2022-01-06 PEUGEOT 208 208 PURETECH 75 1.2 VR3UPHMGBNT001380 1 2022-01-06 HYUNDAI ATOS AH2 ATOS 1.1 MALAF51CANM163805 1 2022-01-06 HYUNDAI ACCENT HCI ACCENT HCI 1.4 MALC741BAMM296216 1 2022-01-03 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA5NC807509 1 2022-01-04 PEUGEOT 2008 2008 PURETECH 130 EAT8 1.2 AUT VR3USHNSSNJ526477 1 2022-01-14 VOLKSWAGEN VOYAGE VOYAGE 1.6 9BWDB45U1NT092231 1 2022-01-06 TOYOTA HILUX HILUX DOBLE CABINA 2.4 8AJJB3DD0N4234313 1 2022-01-06 FORD TERRITORY TERRITORY TREND 1.5 AT LJXCU2BB5NTF05652 1 2022-01-06 PEUGEOT 3008 3008 BLUE HDI 130 EAT8 1.5 AUT VF3MCYHZUNS007139 1 2022-01-03 FORD F-150 F150 LARIAT LUXURY 4X4 3.0 1FTFW1E10MFC13923 1 2022-01-14 PEUGEOT 2008 2008 ALLURE BLUEHDI 1.5 AUT VR3UDYHZSNJ533951 1 2022-01-06 TOYOTA HILUX HILUX DOBLE CABINA 2.4 8AJCB3DD9N3909266 1 2022-01-06 TOYOTA RAV4 RAV4 OTTO 2.0 JTMZ43FV9ND104731 1 2022-01-06 TOYOTA FORTUNER FORTUNER SRV 2.7 AUT 8AJCX3GS8N0130793 1 2022-01-06 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJKB3CD3N1635359 1 2022-01-03 TOYOTA YARIS YARIS SEDAN GLI 1.5 MR2B29F32N1235728 1 2022-01-03 TOYOTA YARIS YARIS SEDAN XLI 1.5 MR2B29F33N1236600 1 2022-01-24 TOYOTA HILUX HILUX DOBLE CABINA 2.4 8AJCB3DDXN3909387 1 2022-01-24 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD8N1318234 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 1.2 MALB241CANM091872 1 2022-01-13 CHEVROLET ONIX ONIX HB RS 1.OT 9BGEN48K0NG135804 1 2022-01-06 PEUGEOT 5008 5008 ALLURE 1.5 AUT VF3MCYHZUNL001187 1 2022-01-04 RENAULT OROCH OROCH 2.0 93Y9SR5A6NJ126126 1 2022-01-06 PEUGEOT 2008 2008 PURETECH 130 1.2 VR3USHNSKNJ526158 1 2022-01-06 PEUGEOT 208 208 BLUE HDI 100 4X2 1.5 VR3UBYHTKNT002161 1 2022-01-03 HYUNDAI VERNA VERNA CB 1.4 LBECBACB2NW163888 1 2022-01-06 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM236453 1 2022-01-06 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM236460 1 2022-01-14 TOYOTA HILUX HI LUX 2.4 8AJJB3DDXN4234822 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM235825 1 2022-01-24 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MT PLUS MALB251CANM236448 1 2022-01-06 PEUGEOT 301 301 HDI 92HP 1.6 VF3DD9HP0NJ524448 1 2022-01-07 CHEVROLET SILVERADO SILVERADO DCAB 4X4 5.3 AT 3GCPY9ED1MG463502 1 2022-01-14 CHEVROLET TRACKER TRACKER 1.2T AUT 9BGEN76C0NB143586 1 2022-01-07 PEUGEOT PARTNER PARTNER HDI 92 L1 1.6 VR3EF9HPANJ530938 1 2022-01-07 PEUGEOT PARTNER PARTNER HDI 92 L1 1.6 VR3EF9HPANJ530936 1 2022-01-07 PEUGEOT PARTNER PARTNER HDI 92 L2 1.6 VR3EF9HPANJ528709 1 2022-01-04 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJKB3CD9N1635785 1 2022-01-07 CHEVROLET SILVERADO SILVERADO CC DCAB 4X4 5.3 AUT 3GCPY9ED9MG460654 1 2022-01-24 CHEVROLET TRACKER TRACKER 1.2T AUT 9BGEN76C0NB142181 1 2022-01-24 FORD TERRITORY TERRITORY TREND GTDI 1.5 AT LJXCU2BB4NTF07151 1 2022-01-24 FORD TERRITORY TERRITORY TREND GTDI 1.5 AT LJXCU2BB5NTF04999 1 2022-01-13 HYUNDAI TUCSON NX4 TUCSON NX4 GDI 7DCT 1.6 AUT KMHJB81BGNU101161 1 2022-01-24 TOYOTA YARIS GR YARIS TURBO 4X4 1.6 JTDAF4E35NA014698 1 2022-01-13 PEUGEOT 2008 2008 ACTI

#**Atualização dos dados semanais**
Como o CSV das vendas semanais estava desatualizado, foi nos passado outro arquivo com as atualizações até o dia 10/09
 Novamente, foi criada a coluna Data e atualização dos nomes das Colunas
 ----------
 Dados atualizados são de extrema importancia para que as consultas e os dados finais sejam os mais fieis possíveis, facilitando assim o trabalho dos tomadores de decisão.

In [0]:
#atualização dados semanais
dados_semanais_att = spark.read.options(sep =";", header=True, encoding = "UTF-8").csv("/mnt/blobed/modulo_02/detran/semanal/2022_09_13_detransemanal.csv")

display(dados_semanais_att)

mes marca modelo versao dia ano vin 9 CHEVROLET TRACKER TRACKER 1.2T AUT 5 2022 9BGEP76C0PB135070 9 CHEVROLET TRACKER TRACKER 1.2T 5 2022 9BGEA76C0PB123327 9 CHEVROLET TRACKER TRACKER 1.2T 5 2022 9BGEA76C0PB134732 9 FORD NEW RANGER RANGER ICA DSL LIMITED 4X4 3.2L 5 2022 8AFAR23W9PJ298163 9 FORD NEW RANGER RANGER ICA DSL LIMITED 4X4 3.2L AT 5 2022 8AFAR23W1PJ288565 9 FORD NEW RANGER RANGER RAPTOR 2.0 DIESEL 5 2022 MPBUR2361NX380342 9 FORD NEW RANGER RANGER ICA DSL XLT 4X2 3.2L 5 2022 8AFAR22W8PJ296969 9 CHEVROLET TRACKER TRACKER 1.2T AUT 5 2022 9BGEP76C0PB137255 9 TOYOTA RAIZE RAIZE CVT 1.2 AUT 2 2022 MHKAB1BA4NJ017854 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA6PC801995 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA2PC803856 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA4PC803860 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG3N0053998 9 HYUNDAI VENUE VENUE QX 1.6 5 2022 KMHRC812APU192190 9 CHEVROLET TRACKER TRACKER 1.2T AUT 5 2022 9BGEP76C0PB124257 9 CHEVROLET TRACKER TRACKER 1.2T 5 2022 9BGEA76C0PB122027 9 TOYOTA RAV4 RAV4 4X4 OTTO 2.0 2 2022 JTMB43FV8PD035874 9 VOLKSWAGEN TOUAREG TOUAREG 4X4 3.0 AT 2 2022 WVGZZZCRZND021792 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA3PC803879 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA4PC800943 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG4N0054089 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAGXN0054081 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG1N0053854 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG5N0055011 9 CHEVROLET N400 MAX N400 MAX 1.5 2 2022 LZWCDAGA6PC800880 9 PEUGEOT 3008 3008 BLUE HDI 130 EAT8 1.5 AUT 2 2022 VF3MCYHZUPS005278 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG8N0054743 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG3N0054696 9 PEUGEOT LANDTREK LANDTREK 4X4 1.9 2 2022 VR3FDAHDLN3006932 9 PEUGEOT BOXER BOXER HDI L3 2.0 2 2022 VF3YD3MAUP2U46642 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG6N0052988 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG2P0058080 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG5N0054246 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG3N0054164 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG0N0054140 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG7N0054040 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG8N0054015 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG0N0053909 9 PEUGEOT 3008 3008 PURETECH 180 EAT8 1.6 AUT 2 2022 VF3M45GFUPS006157 9 PEUGEOT 5008 5008 THP 165 1.6 AUT 2 2022 VF3M45GYWPS004536 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG1N0055068 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG0N0054736 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG9N0054413 9 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 2 2022 9BRK4AAG1N0054258 9 VOLKSWAGEN AMAROK AMAROK DCAB TDI 4X4 TRENDLINE 2.0 5 2022 WV1ZZZ2HZNA021735 9 CHEVROLET TRACKER TRACKER 1.2T AUT 5 2022 9BGEP76C0PB118194 9 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 5 2022 9BG148MK0PC403855 9 FIAT PULSE PULSE IMPETUS TF200 1.0 AUT 5 2022 9BD363B32PYZ20015 9 PEUGEOT BOXER BOXER HDI L2H2 2.0 5 2022 VF3YD3MFBP2V27632 9 CHEVROLET TRACKER TRACKER 1.2T 5 2022 9BGEA76C0PB137038 9 CHEVROLET GROOVE GROOVE 1.5 5 2022 LZWADAGA5PG002726 9 FIAT PULSE PULSE DRIVE HB 1.3 AUT 5 2022 9BD363B16PYZ36151 9 CHEVROLET N400 MAX N400 MAX 1.5 5 2022 LZWCDAGA1PC800866 9 CHEVROLET SILVERADO SILVERADO 4X4 CC 5.3 AUT 5 2022 3GCUD9ED1NG563843 9 TOYOTA RAV4 RAV4 OTTO 2.0 AUT 5 2022 JTMZ43FV2PD132986 9 CHEVROLET ONIX ONIX HB RS 1.0T 5 2022 9BGEN48K0PG138072 9 PEUGEOT BOXER BOXER HDI L2H2 2.0 2 2022 VF3YD3MFBP2U93703 9 CHEVROLET TRACKER TRACKER 1.2T 5 2022 9BGEN76C0PB102096 9 CHEVROLET TRACKER TRACKER 1.2T AUT 5 2022 9BGEN76C0PB118563 9 CHEVROLET TRACKER TRACKER 1.2T AUT 5 2022 9BGEP76C0PB125

In [0]:
#Atualização dos dados
#Cria coluna data
#Edita o nome das outras colunas
dados_semanais_att_data = dados_semanais_att.select(\
    concat_ws('-',dados_semanais_att.ano, dados_semanais_att.mes, dados_semanais_att.dia)\
    .alias("Data"), "Marca", "Modelo", "Versao", "Vin", "Mes")

#Converte a nova coluna (Data) no tipo date
dados_semanais_att_data = dados_semanais_att_data.withColumn("Data", col("Data").cast("date"))

display(dados_semanais_att_data)

Data Marca Modelo Versao Vin Mes 2022-09-05 CHEVROLET TRACKER TRACKER 1.2T AUT 9BGEP76C0PB135070 9 2022-09-05 CHEVROLET TRACKER TRACKER 1.2T 9BGEA76C0PB123327 9 2022-09-05 CHEVROLET TRACKER TRACKER 1.2T 9BGEA76C0PB134732 9 2022-09-05 FORD NEW RANGER RANGER ICA DSL LIMITED 4X4 3.2L 8AFAR23W9PJ298163 9 2022-09-05 FORD NEW RANGER RANGER ICA DSL LIMITED 4X4 3.2L AT 8AFAR23W1PJ288565 9 2022-09-05 FORD NEW RANGER RANGER RAPTOR 2.0 DIESEL MPBUR2361NX380342 9 2022-09-05 FORD NEW RANGER RANGER ICA DSL XLT 4X2 3.2L 8AFAR22W8PJ296969 9 2022-09-05 CHEVROLET TRACKER TRACKER 1.2T AUT 9BGEP76C0PB137255 9 2022-09-02 TOYOTA RAIZE RAIZE CVT 1.2 AUT MHKAB1BA4NJ017854 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA6PC801995 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA2PC803856 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA4PC803860 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG3N0053998 9 2022-09-05 HYUNDAI VENUE VENUE QX 1.6 KMHRC812APU192190 9 2022-09-05 CHEVROLET TRACKER TRACKER 1.2T AUT 9BGEP76C0PB124257 9 2022-09-05 CHEVROLET TRACKER TRACKER 1.2T 9BGEA76C0PB122027 9 2022-09-02 TOYOTA RAV4 RAV4 4X4 OTTO 2.0 JTMB43FV8PD035874 9 2022-09-02 VOLKSWAGEN TOUAREG TOUAREG 4X4 3.0 AT WVGZZZCRZND021792 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA3PC803879 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA4PC800943 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG4N0054089 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAGXN0054081 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG1N0053854 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG5N0055011 9 2022-09-02 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA6PC800880 9 2022-09-02 PEUGEOT 3008 3008 BLUE HDI 130 EAT8 1.5 AUT VF3MCYHZUPS005278 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG8N0054743 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG3N0054696 9 2022-09-02 PEUGEOT LANDTREK LANDTREK 4X4 1.9 VR3FDAHDLN3006932 9 2022-09-02 PEUGEOT BOXER BOXER HDI L3 2.0 VF3YD3MAUP2U46642 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG6N0052988 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG2P0058080 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG5N0054246 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG3N0054164 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG0N0054140 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG7N0054040 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG8N0054015 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG0N0053909 9 2022-09-02 PEUGEOT 3008 3008 PURETECH 180 EAT8 1.6 AUT VF3M45GFUPS006157 9 2022-09-02 PEUGEOT 5008 5008 THP 165 1.6 AUT VF3M45GYWPS004536 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG1N0055068 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG0N0054736 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG9N0054413 9 2022-09-02 TOYOTA COROLLA CROSS COROLLA CROSS CVT 2.0 AUT 9BRK4AAG1N0054258 9 2022-09-05 VOLKSWAGEN AMAROK AMAROK DCAB TDI 4X4 TRENDLINE 2.0 WV1ZZZ2HZNA021735 9 2022-09-05 CHEVROLET TRACKER TRACKER 1.2T AUT 9BGEP76C0PB118194 9 2022-09-05 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 9BG148MK0PC403855 9 2022-09-05 FIAT PULSE PULSE IMPETUS TF200 1.0 AUT 9BD363B32PYZ20015 9 2022-09-05 PEUGEOT BOXER BOXER HDI L2H2 2.0 VF3YD3MFBP2V27632 9 2022-09-05 CHEVROLET TRACKER TRACKER 1.2T 9BGEA76C0PB137038 9 2022-09-05 CHEVROLET GROOVE GROOVE 1.5 LZWADAGA5PG002726 9 2022-09-05 FIAT PULSE PULSE DRIVE HB 1.3 AUT 9BD363B16PYZ36151 9 2022-09-05 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA1PC800866 9 2022-09-05 CHEVROLET SILVERADO SILVERADO 4X4 CC 5.3 AUT 3GCUD9ED1NG563843 9 2022-09-05 TOYOTA RAV4 RAV4 OTTO 2.0 AUT JTMZ43FV2PD132986 9 2022-09-05 CHEVROLET ONIX ONIX HB RS 1.0T 9BGEN48K0PG138072 9 2022-09-02 PEUGEO

In [0]:
#Join dados semanais e dados semanais novos
dados_set_totais = dados_semanais_data.join(dados_semanais_att_data,['Mes','Data', 'Marca', 'Modelo', 'Versao', 'Vin'],'outer')

display(dados_set_totais)

Mes Data Marca Modelo Versao Vin 9 2022-09-01 BMW X6 X6 M50I 4X4 4.4 AUT WBACY8103N9L11585 9 2022-09-01 CHEVROLET CAPTIVA CAPTIVA MT6 4X2 1.5 LZWADAGA3PB009929 9 2022-09-01 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 9BG148FK0PC408873 9 2022-09-01 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 9BG148FK0PC408966 9 2022-09-01 CHEVROLET GROOVE GROOVE 1.5 LZWADAGA5PG003665 9 2022-09-01 CHEVROLET GROOVE GROOVE PREMIER 1.5 LZWADAGA0NG021925 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA0PC802415 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA1PC802231 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA1PC803802 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA4PC803826 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA5PC801017 9 2022-09-01 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA9PC803787 9 2022-09-01 CHEVROLET NPR NPR 816 VL20 JAANPR75KP7100218 9 2022-09-01 CHEVROLET ONIX ONIX HB RS 1.OT 9BGED48K0PG156990 9 2022-09-01 CHEVROLET ONIX ONIX HB RS 1.OT 9BGED48K0PG160330 9 2022-09-01 CHEVROLET TRACKER TRACKER 1.2T AUT 9BGEN76C0PB123591 9 2022-09-01 CHEVROLET TRACKER TRACKER 1.2T LS MT P 9BGEA76C0PB135857 9 2022-09-01 FIAT PULSE PULSE DRIVE MT 1.3 9BD363B14PYZ16404 9 2022-09-01 FORD TERRITORY TERRITORY 1.5 AUT LJXCU2BB6NTF15753 9 2022-09-01 FORD TERRITORY TERRITORY 1.5 AUT LJXCU2BB6NTF15767 9 2022-09-01 HYUNDAI EX 9 EX9 EXTRA KMFHA17HPPC069539 9 2022-09-01 HYUNDAI GRAND I-10 GRAND I10 HB 1.2 MALB251CAPM324452 9 2022-09-01 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MT PLUS MALB251CAPM324189 9 2022-09-01 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 MALB241CAPM119904 9 2022-09-01 HYUNDAI HD 35 HD 35 LWB 2.5 KMFVA17RPNC360146 9 2022-09-01 HYUNDAI HD 35 HD35 SWB 2P 2.5 KMFVA17RPPC360548 9 2022-09-01 HYUNDAI HD 35 HD35 SWB 2P 2.5 KMFVA17RPPC360549 9 2022-09-01 HYUNDAI NEW CRETA CRETA 1.5 MALPB812APM309405 9 2022-09-01 HYUNDAI VENUE VENUE QX 1.6 MT VALUE KMHRC812APU192146 9 2022-09-01 PEUGEOT 2008 2008 PURETECH 130 1.2 VR3USHNSKPJ513630 9 2022-09-01 RENAULT DUSTER DUSTER 4X2 1.6 VF1HJD205PA283373 9 2022-09-01 RENAULT DUSTER DUSTER 4X2 1.6 VF1HJD206PA260023 9 2022-09-01 TOYOTA COROLLA CROSS COROLLA CROSS SEG 2.0 9BRK4AAG5P0057859 9 2022-09-01 TOYOTA HILUX HILUX 4X2 2.4 MT SR 8AJJB3DD1P4237160 9 2022-09-01 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD9P1326670 9 2022-09-01 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJKB3CD6N1641785 9 2022-09-01 TOYOTA HILUX NEW HILUX 4X4 2.4L MT DX 8AJDB3C5P1325144 9 2022-09-01 TOYOTA RAV4 RAV4 LE 2.0 4X2 CVT JTMZ43FV0PD133196 9 2022-09-01 TOYOTA RAV4 RAV4 LE 2.0 4X2 MT JTMZ43FV9PD132421 9 2022-09-01 TOYOTA YARIS YARIS HB OTTO 1.5 MR2K29F35N1249820 9 2022-09-01 TOYOTA YARIS YARIS SEDAN GLI 1.5 MT MR2B29F38N1242070 9 2022-09-01 TOYOTA YARIS YARIS SEDAN OTTO 1.5 MR2B29F3XN1251207 9 2022-09-01 TOYOTA YARIS YARIS SEDAN XLI 1.5 TM MR2B29F37N1249172 9 2022-09-01 VOLKSWAGEN GOL GOL HB 1.6 9BWAB45U2NT122386 9 2022-09-01 VOLKSWAGEN GOL GOL HB 1.6 9BWAB45U5NT122446 9 2022-09-01 VOLKSWAGEN GOL GOL HB 1.6 9BWAB45U7NT120908 9 2022-09-01 VOLKSWAGEN GOL GOL HB 1.6 9BWAB45U7NT122948 9 2022-09-01 VOLKSWAGEN GOL GOL HB 1.6 9BWAB45U8NT091368 9 2022-09-01 VOLKSWAGEN NUEVO VIRTUS VIRTUS OTTO 1.6 9BWDL5BZ3NP040160 9 2022-09-01 VOLKSWAGEN POLO POLO HATCH BACK 1.6 AT 9BWAL5BZ8NP039783 9 2022-09-01 VOLKSWAGEN SAVEIRO SAVEIRO CS 1.6 9BWKL45UXNP046264 9 2022-09-01 VOLKSWAGEN T-CROSS T CROSS TSI 1.0 AUT 9BWBH6BF7N4066511 9 2022-09-01 VOLKSWAGEN VOYAGE VOYAGE 1.6 9BWDB45U9NT127906 9 2022-09-02 CHEVROLET CAPTIVA CAPTIVA MT6 4X2 1.5 LZWADAGA3PB010689 9 2022-09-02 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 9BG148FK0PC409163 9 2022-09-02 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 9BG148FK0PC409300 9 2022-09-02 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 9BG148MK0PC407708 9 2022-09-02 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 9BG148PK0PC408616 9 2022-09-02 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 9BG148PK0PC408842 9 2022-09-02 CHEVROLET GROOVE GROOVE 1.5 LZWADAGA1PG004599 9 2022-09-02 CHEVROLET GROOVE GROOVE 1.5 LZWADAGA3PG

In [0]:
dados_totais = dados_set_totais.join(dados_mensais_data,['Mes','Data', 'Marca', 'Modelo', 'Versao', 'Vin'],'outer')
display(dados_totais)

Mes Data Marca Modelo Versao Vin 1 2022-01-03 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 9BG148MK0NC431959 1 2022-01-03 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 9BG148PK0NC431083 1 2022-01-03 CHEVROLET GROOVE GROOVE LTZ 1.5 LZWADAGA2NG005841 1 2022-01-03 CHEVROLET GROOVE GROOVE LTZ 1.5 LZWADAGA7NG006144 1 2022-01-03 CHEVROLET GROOVE GROOVE PREMIER 1.5 LZWADAGA1NG007063 1 2022-01-03 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA1NC808169 1 2022-01-03 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA3NC807556 1 2022-01-03 CHEVROLET SAIL SAIL 1.5 LSGHD52H1ND024884 1 2022-01-03 CHEVROLET SAIL SAIL 1.5 LSGHD52H1ND025050 1 2022-01-03 CHEVROLET SILVERADO SILVERADO DCAB 4X4 5.3 AT 3GCPY9ED6MG465102 1 2022-01-03 FORD ECOSPORT ECOSPORT 1.5 AT MAJBMSMCKNMG55360 1 2022-01-03 FORD F-150 F150 LARIAT LUXURY 4X4 3.0 1FTFW1E10MFC13923 1 2022-01-03 FORD NEW RANGER RANGER RAPTOR 4X4 2.0 AUT MPBUR2366NX355694 1 2022-01-03 FORD NEW RANGER RANGER XLS 4X4 3.2 8AFAR23W2NJ256057 1 2022-01-03 FORD TERRITORY TERRITORY TREND 1.5 AUT LJXCU2BB3NTP03448 1 2022-01-03 FORD TRANSIT VAN TRANSIT CUSTOM FURGON 2.2 WF0YXXTTGNTA25320 1 2022-01-03 HYUNDAI ACCENT HCI ACCENT HCI 1.4 MALC741BAMM296983 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 1.2 MALB241CANM091872 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM235825 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM236461 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM236514 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM238134 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM239573 1 2022-01-03 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 MALB241CANM091900 1 2022-01-03 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 MALB241CANM096489 1 2022-01-03 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 MALB241CANM096500 1 2022-01-03 HYUNDAI HD 35 HD 35 LWB 2.5 KMFVA17RPNC356644 1 2022-01-03 HYUNDAI HD 35 HD 35 LWB 2.5 KMFVA17RPNC356650 1 2022-01-03 HYUNDAI I20 BI3 I20 BI3 1.4 MALBG513AMM036399 1 2022-01-03 HYUNDAI SOLATI H350 2.5 KMFAB17RPNK024493 1 2022-01-03 HYUNDAI STARIA MB STARIA US4 CRDI 2.2 KMJYA371ANU029301 1 2022-01-03 HYUNDAI STARIA MB STARIA US4 CRDI 2.2 AUT KMHYB811BNU031978 1 2022-01-03 HYUNDAI TUCSON NX4 TUCSON NX4 MPI 2.0 KMHJB81DANU099776 1 2022-01-03 HYUNDAI VENUE VENUE QX 1.6 KMHRC812ANU144131 1 2022-01-03 HYUNDAI VERNA VERNA CB 1.4 LBECBACB9NW165721 1 2022-01-03 PEUGEOT 2008 2008 BLUE HDI 100 4X2 1.5 VR3UDYHSKNJ529068 1 2022-01-03 PEUGEOT 2008 2008 PURETECH 130 EAT8 1.2 AUT VR3USHNSSNJ525794 1 2022-01-03 PEUGEOT 208 208 PURETECH 75 1.2 VR3UPHMGBNT001463 1 2022-01-03 PEUGEOT 208 208 PURETECH 75 1.2 VR3UPHMGBNT001576 1 2022-01-03 PEUGEOT 208 208 PURETECH 75 1.2 VR3UPHMGBNT002011 1 2022-01-03 PEUGEOT 3008 3008 BLUE HDI 130 1.5 VF3MCYHZMNS007648 1 2022-01-03 PEUGEOT PARTNER PARTNER HDI 92 L1 1.6 VR3EF9HPANJ521050 1 2022-01-03 RENAULT OROCH OROCH ZEN MT 1.6 93Y9SR0SENJ126078 1 2022-01-03 TOYOTA COROLLA CROSS COROLLA CROSS CVT HEV 1.8 AUT 9BRKZAAG9N0619955 1 2022-01-03 TOYOTA FORTUNER FORTUNER 4X4 5P 2.8 AUT 8AJDA3FS1N0504152 1 2022-01-03 TOYOTA HILUX HILUX DOBLE CABINA 2.4 8AJCB3DD0N3909348 1 2022-01-03 TOYOTA HILUX HILUX PICK UP 4X4 2P 2.4 8AJDB8CB8N5511794 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJCB3DDXN3908417 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD0N1317952 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD1N1317538 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD2N1317550 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD4N1317646 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD5N1317042 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD5N1317526 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD6N1317521 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD6N1317535 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD8N1317617 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3C

#**Consultas**
Neste bloco, foram realizadas algumas consultas com os dados já tratados acima.
* Quantidade de vendas por mes;
* Marcas e Modelos mais vendidos;
* Quanto, especificamente, a marca Fiat vendeu no decorrer dos meses.
---------
Como já explicitado acima, a confiabilidade dos dados é muito importante pois através deles é que podemos entregar a necessidade do cliente.

In [0]:
# selecionando quantas vendas existem em cada mês:
vendas_por_mes = dados_totais.groupBy('Mes').count() \
    .withColumnRenamed('count','Qntde_vendida')

vendas_por_mes = vendas_por_mes.orderBy('Mes')

display(vendas_por_mes)

Mes Qntde_vendida 1 5453 2 4604 3 5845 4 5740 5 5496 6 6272 7 5885 8 5358 9 1224

In [0]:
#ver quantas marcas diferentes existem no dataframe 
display(dados_totais.select('Marca').distinct())

#Agrupando a quantidade de carros vendidos em cada marca e modelo
vendas = dados_totais.groupBy('Marca', 'Modelo').count().withColumnRenamed('count', 'Qntde_vendidos')
display(vendas.head(1))

Marca HYUNDAI FIAT TOYOTA FORD PEUGEOT CHEVROLET BMW VOLKSWAGEN RENAULT

Marca Modelo Qntde_vendidos PEUGEOT LANDTREK 509

In [0]:
#Qual a quantidade de vendas de Fiats ao longo do ano?
vendas_fiat = dados_totais.groupBy("Marca", 'Mes').count()
vendas_fiat = vendas_fiat.select('Mes', 'count') \
    .where(dados_totais.Marca == "FIAT") \
    .withColumnRenamed('count', 'Qntde_Vendida') \
    .orderBy('Mes')
display(vendas_fiat)

Mes Qntde_Vendida 1 8 2 27 3 8 4 36 5 150 6 139 7 54 8 39 9 25

In [0]:
#Filtrar os dados para o primeiro semestre 
# Agrupar os dados por marca e modelo (a contagem de vin’s dará o número de veículos vendidos para o consumidor final)
dados_totais_prSemestre = dados_totais.where("Mes < '7'")
display(dados_totais_prSemestre)

Mes Data Marca Modelo Versao Vin 1 2022-01-03 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 9BG148MK0NC431959 1 2022-01-03 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT 9BG148PK0NC431083 1 2022-01-03 CHEVROLET GROOVE GROOVE LTZ 1.5 LZWADAGA2NG005841 1 2022-01-03 CHEVROLET GROOVE GROOVE LTZ 1.5 LZWADAGA7NG006144 1 2022-01-03 CHEVROLET GROOVE GROOVE PREMIER 1.5 LZWADAGA1NG007063 1 2022-01-03 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA1NC808169 1 2022-01-03 CHEVROLET N400 MAX N400 MAX 1.5 LZWCDAGA3NC807556 1 2022-01-03 CHEVROLET SAIL SAIL 1.5 LSGHD52H1ND024884 1 2022-01-03 CHEVROLET SAIL SAIL 1.5 LSGHD52H1ND025050 1 2022-01-03 CHEVROLET SILVERADO SILVERADO DCAB 4X4 5.3 AT 3GCPY9ED6MG465102 1 2022-01-03 FORD ECOSPORT ECOSPORT 1.5 AT MAJBMSMCKNMG55360 1 2022-01-03 FORD F-150 F150 LARIAT LUXURY 4X4 3.0 1FTFW1E10MFC13923 1 2022-01-03 FORD NEW RANGER RANGER RAPTOR 4X4 2.0 AUT MPBUR2366NX355694 1 2022-01-03 FORD NEW RANGER RANGER XLS 4X4 3.2 8AFAR23W2NJ256057 1 2022-01-03 FORD TERRITORY TERRITORY TREND 1.5 AUT LJXCU2BB3NTP03448 1 2022-01-03 FORD TRANSIT VAN TRANSIT CUSTOM FURGON 2.2 WF0YXXTTGNTA25320 1 2022-01-03 HYUNDAI ACCENT HCI ACCENT HCI 1.4 MALC741BAMM296983 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 1.2 MALB241CANM091872 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM235825 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM236461 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM236514 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM238134 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 MALB251CANM239573 1 2022-01-03 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 MALB241CANM091900 1 2022-01-03 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 MALB241CANM096489 1 2022-01-03 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 MALB241CANM096500 1 2022-01-03 HYUNDAI HD 35 HD 35 LWB 2.5 KMFVA17RPNC356644 1 2022-01-03 HYUNDAI HD 35 HD 35 LWB 2.5 KMFVA17RPNC356650 1 2022-01-03 HYUNDAI I20 BI3 I20 BI3 1.4 MALBG513AMM036399 1 2022-01-03 HYUNDAI SOLATI H350 2.5 KMFAB17RPNK024493 1 2022-01-03 HYUNDAI STARIA MB STARIA US4 CRDI 2.2 KMJYA371ANU029301 1 2022-01-03 HYUNDAI STARIA MB STARIA US4 CRDI 2.2 AUT KMHYB811BNU031978 1 2022-01-03 HYUNDAI TUCSON NX4 TUCSON NX4 MPI 2.0 KMHJB81DANU099776 1 2022-01-03 HYUNDAI VENUE VENUE QX 1.6 KMHRC812ANU144131 1 2022-01-03 HYUNDAI VERNA VERNA CB 1.4 LBECBACB9NW165721 1 2022-01-03 PEUGEOT 2008 2008 BLUE HDI 100 4X2 1.5 VR3UDYHSKNJ529068 1 2022-01-03 PEUGEOT 2008 2008 PURETECH 130 EAT8 1.2 AUT VR3USHNSSNJ525794 1 2022-01-03 PEUGEOT 208 208 PURETECH 75 1.2 VR3UPHMGBNT001463 1 2022-01-03 PEUGEOT 208 208 PURETECH 75 1.2 VR3UPHMGBNT001576 1 2022-01-03 PEUGEOT 208 208 PURETECH 75 1.2 VR3UPHMGBNT002011 1 2022-01-03 PEUGEOT 3008 3008 BLUE HDI 130 1.5 VF3MCYHZMNS007648 1 2022-01-03 PEUGEOT PARTNER PARTNER HDI 92 L1 1.6 VR3EF9HPANJ521050 1 2022-01-03 RENAULT OROCH OROCH ZEN MT 1.6 93Y9SR0SENJ126078 1 2022-01-03 TOYOTA COROLLA CROSS COROLLA CROSS CVT HEV 1.8 AUT 9BRKZAAG9N0619955 1 2022-01-03 TOYOTA FORTUNER FORTUNER 4X4 5P 2.8 AUT 8AJDA3FS1N0504152 1 2022-01-03 TOYOTA HILUX HILUX DOBLE CABINA 2.4 8AJCB3DD0N3909348 1 2022-01-03 TOYOTA HILUX HILUX PICK UP 4X4 2P 2.4 8AJDB8CB8N5511794 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJCB3DDXN3908417 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD0N1317952 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD1N1317538 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD2N1317550 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD4N1317646 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD5N1317042 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD5N1317526 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD6N1317521 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD6N1317535 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD8N1317617 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3C

#**TARGET - Metas primeiro semestre 2022**
Neste bloco foi adicionado o CSV de metas de vendas para o 1º sem. de 2022. Foi feito tratamento dos dados e junção da tabela de vendas com a de target. O objetivo principal desta etapa foi consultar quais marcas atingiram a meta estipulada para o período.

In [0]:
#Leitura csv Target
target = spark.read.options(sep=";", header=True, encoding = "UTF-8").csv("/mnt/blobed/modulo_02/target/target.csv")

#Cast Target Semestre 1 para inteiro 
target = target.withColumn("Target Semestre 1", col("Target Semestre 1").cast("int"))
#Muda o nome da coluna Target Semestre 1 para Target_Semestre_1
target = target.withColumnRenamed('Target Semestre 1', 'Target_Semestre_1')
display(target)

Marca Modelo Target_Semestre_1 BMW 118 2 BMW 218I 4 BMW 220 1 BMW 235 1 BMW 320 2 BMW 330 14 BMW 420 2 BMW 430I 1 BMW 520 3 BMW 530 1 BMW I3 2 BMW X1 1 BMW X2 2 BMW X3 13 BMW X4 3 BMW X5 4 BMW X6 2 CHEVROLET BLAZER 60 CHEVROLET CAMARO 1 CHEVROLET CAPTIVA 1295 CHEVROLET COLORADO 1065 CHEVROLET D-MAX 35 CHEVROLET GROOVE 1468 CHEVROLET N400 MAX 1034 CHEVROLET ONIX 1787 CHEVROLET OPTRA 1 CHEVROLET SAIL 2000 CHEVROLET SILVERADO 304 CHEVROLET SPARK GT 2 CHEVROLET SPIN 353 CHEVROLET SUBURBAN 28 CHEVROLET TAHOE 84 CHEVROLET TRACKER 2487 CHEVROLET TRAILBLAZER 98 CHEVROLET TRAVERSE 97 FIAT ARGO 89 FIAT CASA RODANTE 2 FIAT CINQUECENTO 13 FIAT CRONOS 70 FIAT DUCATO 26 FIAT FIORINO 1 FIAT MOBI 1 FIAT PULSE 100 FORD BRONCO SPORT 85 FORD CASA RODANTE 3 FORD ECOSPORT 121 FORD EDGE 108 FORD EXPEDITION 50 FORD EXPLORER 209 FORD F 350 1 FORD F 450 1 FORD F-150 242 FORD F-250 2 FORD MAVERICK 34 FORD MUSTANG 25 FORD NEW ESCAPE 43 FORD NEW RANGER 509 FORD TERRITORY 542 FORD TRANSIT VAN 152 HYUNDAI ACCENT 2 HYUNDAI ACCENT HCI 352 HYUNDAI ATOS AH2 182 HYUNDAI CRETA 5 HYUNDAI CRETA GRAND SU2I 49 HYUNDAI ELANTRA CN7 99 HYUNDAI GRAND I-10 182 HYUNDAI GRAND I-10 AI3 HB 1.2 150 HYUNDAI GRAND I-10 Ai3 SEDAN 23 HYUNDAI GRAND I-10 SEDAN 48 HYUNDAI H-1 2 HYUNDAI HD 35 292 HYUNDAI I20 BI3 45 HYUNDAI I20 IB 1 HYUNDAI IONIQ 6 HYUNDAI NEW CRETA 195 HYUNDAI PALISADE LX2 11 HYUNDAI PORTER 463 HYUNDAI SANTA FE TM 122 HYUNDAI SANTA FE TM FL 16 HYUNDAI SOLATI 160 HYUNDAI STARIA FG 9 HYUNDAI STARIA MB 81 HYUNDAI TUCSON NX4 5 HYUNDAI TUCSON TL 9 HYUNDAI VELOSTER 9 HYUNDAI VENUE 238 HYUNDAI VERNA 203 PEUGEOT 2008 769 PEUGEOT 208 544 PEUGEOT 3008 1009 PEUGEOT 301 396 PEUGEOT 308 11 PEUGEOT 5008 287 PEUGEOT BOXER 198 PEUGEOT EXPERT 210 PEUGEOT LANDTREK 207 PEUGEOT PARTNER 1773 PEUGEOT RIFTER 119 PEUGEOT SIN MODELO 1 RENAULT ARKANA 13 RENAULT CLIO V 31 RENAULT DOKKER 64 RENAULT DUSTER 96 RENAULT EXPRESS 52 RENAULT KANGOO 2 RENAULT KOLEOS 6 RENAULT KWID 94 RENAULT OROCH 21 RENAULT SYMBOL 30 TOYOTA 4RUNNER 190 TOYOTA C-HR 8 TOYOTA COROLLA 176 TOYOTA COROLLA CROSS 655 TOYOTA FORTUNER 5 TOYOTA HIACE 6 TOYOTA HILUX 1723 TOYOTA LAND CRUISER 28 TOYOTA PRIUS 4 TOYOTA RAIZE 467 TOYOTA RAV4 1606 TOYOTA RUSH 467 TOYOTA TACOMA 1 TOYOTA YARIS 1258 VOLKSWAGEN AMAROK 173 VOLKSWAGEN CASA RODANTE 2 VOLKSWAGEN GOL 616 VOLKSWAGEN NIVUS 169 VOLKSWAGEN NUEVO VIRTUS 1 VOLKSWAGEN POLO 100 VOLKSWAGEN SAVEIRO 248 VOLKSWAGEN TAOS 161 VOLKSWAGEN T-CROSS 471 VOLKSWAGEN TIGUAN 21 VOLKSWAGEN VOYAGE 269

In [0]:
#vendas -> quantidade de carros vendidos de cada marca e modelo
#Fazer um join entre a tabela de target com a tabela de vendas
target_vendas = vendas.join(target, on = ['Marca', 'Modelo'], how='outer')
target_vendas = target_vendas.withColumnRenamed('count', 'Qntde_vendida')
display(target_vendas)

Marca Modelo Qntde_vendidos Target_Semestre_1 BMW 118 2 2 BMW 218I 4 4 BMW 220 1 1 BMW 235 1 1 BMW 320 4 2 BMW 330 15 14 BMW 420 2 2 BMW 430I 1 1 BMW 520 3 3 BMW 530 1 1 BMW I3 2 2 BMW X1 12 1 BMW X2 3 2 BMW X3 20 13 BMW X4 4 3 BMW X5 5 4 BMW X6 3 2 BMW X7 1 null CHEVROLET BLAZER 75 60 CHEVROLET CAMARO 2 1 CHEVROLET CAPTIVA 1551 1295 CHEVROLET COLORADO 1498 1065 CHEVROLET D-MAX 35 35 CHEVROLET FTR 1 null CHEVROLET FVR 1 null CHEVROLET GROOVE 1913 1468 CHEVROLET N400 MAX 1394 1034 CHEVROLET NKR 1 null CHEVROLET NPR 6 null CHEVROLET NQR 3 null CHEVROLET ONIX 2167 1787 CHEVROLET OPTRA 1 1 CHEVROLET SAIL 3285 2000 CHEVROLET SILVERADO 346 304 CHEVROLET SPARK GT 3 2 CHEVROLET SPIN 433 353 CHEVROLET SUBURBAN 41 28 CHEVROLET TAHOE 94 84 CHEVROLET TRACKER 3882 2487 CHEVROLET TRAILBLAZER 130 98 CHEVROLET TRAVERSE 130 97 FIAT 595 2 null FIAT ARGO 106 89 FIAT CASA RODANTE 2 2 FIAT CINQUECENTO 15 13 FIAT CRONOS 81 70 FIAT DUCATO 41 26 FIAT FIORINO 3 1 FIAT MOBI 2 1 FIAT PULSE 234 100 FORD BRONCO SPORT 117 85 FORD CASA RODANTE 5 3 FORD ECOSPORT 121 121 FORD EDGE 162 108 FORD EXPEDITION 5 50 FORD EXPLORER 278 209 FORD F 350 1 1 FORD F 450 1 1 FORD F-150 248 242 FORD F-250 2 2 FORD MAVERICK 83 34 FORD MUSTANG 31 25 FORD NEW ESCAPE 81 43 FORD NEW RANGER 617 509 FORD TERRITORY 799 542 FORD TRANSIT VAN 237 152 HYUNDAI ACCENT 2 2 HYUNDAI ACCENT HCI 398 352 HYUNDAI ATOS AH2 326 182 HYUNDAI COUNTY 2 null HYUNDAI CRETA 17 5 HYUNDAI CRETA GRAND SU2I 68 49 HYUNDAI ELANTRA CN7 107 99 HYUNDAI EX 9 1 null HYUNDAI GRAND I-10 346 182 HYUNDAI GRAND I-10 AI3 HB 1.2 186 150 HYUNDAI GRAND I-10 Ai3 SEDAN 49 23 HYUNDAI GRAND I-10 SEDAN 109 48 HYUNDAI H-1 3 2 HYUNDAI HD 35 371 292 HYUNDAI I20 BI3 71 45 HYUNDAI I20 IB 5 1 HYUNDAI IONIQ 6 6 HYUNDAI KONA 2 null HYUNDAI MIGHTY EX6 1 null HYUNDAI MIGHTY EX8 5 null HYUNDAI NEW CRETA 345 195 HYUNDAI PALISADE LX2 18 11 HYUNDAI PORTER 517 463 HYUNDAI SANTA FE TM 140 122 HYUNDAI SANTA FE TM FL 17 16 HYUNDAI SOLATI 210 160 HYUNDAI STARIA FG 12 9 HYUNDAI STARIA MB 106 81 HYUNDAI TUCSON NX4 597 5 HYUNDAI TUCSON TL 12 9 HYUNDAI VELOSTER 12 9 HYUNDAI VENUE 294 238 HYUNDAI VERNA 204 203 PEUGEOT 2008 1027 769 PEUGEOT 208 611 544 PEUGEOT 3008 1311 1009 PEUGEOT 301 591 396 PEUGEOT 308 226 11 PEUGEOT 5008 344 287 PEUGEOT BOXER 275 198 PEUGEOT EXPERT 310 210 PEUGEOT LANDTREK 509 207 PEUGEOT PARTNER 2129 1773 PEUGEOT RIFTER 202 119 PEUGEOT SIN MODELO 1 1 RENAULT ARKANA 15 13 RENAULT C 1 null RENAULT CLIO V 31 31 RENAULT DOKKER 64 64 RENAULT DUSTER 111 96 RENAULT EXPRESS 179 52 RENAULT KANGOO 2 2 RENAULT KOLEOS 6 6 RENAULT KWID 120 94 RENAULT OROCH 32 21 RENAULT SYMBOL 31 30 TOYOTA 4RUNNER 204 190 TOYOTA C-HR 13 8 TOYOTA COROLLA 233 176 TOYOTA COROLLA CROSS 951 655 TOYOTA FORTUNER 132 5 TOYOTA HIACE 8 6 TOYOTA HILUX 2362 1723 TOYOTA LAND CRUISER 39 28 TOYOTA PRIUS 5 4 TOYOTA RAIZE 840 467 TOYOTA RAV4 2226 1606 TOYOTA RUSH 604 467 TOYOTA TACOMA 1 1 TOYOTA YARIS 1700 1258 VOLKSWAGEN AMAROK 194 173 VOLKSWAGEN CASA RODANTE 2 2 VOLKSWAGEN CONSTELLATION 19 null VOLKSWAGEN DELIVERY 1 null VOLKSWAGEN GOL 1005 616 VOLKSWAGEN NIVUS 183 169 VOLKSWAGEN NUEVO VIRTUS 51 1 VOLKSWAGEN POLO 84 100 VOLKSWAGEN SAVEIRO 481 248 VOLKSWAGEN T-CROSS 578 471 VOLKSWAGEN TAOS 186 161 VOLKSWAGEN TIGUAN 27 21 VOLKSWAGEN TOUAREG 1 null VOLKSWAGEN VOYAGE 710 269

In [0]:
#Com a tabela construída, responder: Quais as marcas que atingiraram a meta de vendas para o semestre de 2022?
meta_atingida = target_vendas.where("Qntde_vendidos >= Target_Semestre_1").orderBy('Marca', 'Modelo')
display(meta_atingida)

Marca Modelo Qntde_vendidos Target_Semestre_1 BMW 118 2 2 BMW 218I 4 4 BMW 220 1 1 BMW 235 1 1 BMW 320 4 2 BMW 330 15 14 BMW 420 2 2 BMW 430I 1 1 BMW 520 3 3 BMW 530 1 1 BMW I3 2 2 BMW X1 12 1 BMW X2 3 2 BMW X3 20 13 BMW X4 4 3 BMW X5 5 4 BMW X6 3 2 CHEVROLET BLAZER 75 60 CHEVROLET CAMARO 2 1 CHEVROLET CAPTIVA 1551 1295 CHEVROLET COLORADO 1498 1065 CHEVROLET D-MAX 35 35 CHEVROLET GROOVE 1913 1468 CHEVROLET N400 MAX 1394 1034 CHEVROLET ONIX 2167 1787 CHEVROLET OPTRA 1 1 CHEVROLET SAIL 3285 2000 CHEVROLET SILVERADO 346 304 CHEVROLET SPARK GT 3 2 CHEVROLET SPIN 433 353 CHEVROLET SUBURBAN 41 28 CHEVROLET TAHOE 94 84 CHEVROLET TRACKER 3882 2487 CHEVROLET TRAILBLAZER 130 98 CHEVROLET TRAVERSE 130 97 FIAT ARGO 106 89 FIAT CASA RODANTE 2 2 FIAT CINQUECENTO 15 13 FIAT CRONOS 81 70 FIAT DUCATO 41 26 FIAT FIORINO 3 1 FIAT MOBI 2 1 FIAT PULSE 234 100 FORD BRONCO SPORT 117 85 FORD CASA RODANTE 5 3 FORD ECOSPORT 121 121 FORD EDGE 162 108 FORD EXPLORER 278 209 FORD F 350 1 1 FORD F 450 1 1 FORD F-150 248 242 FORD F-250 2 2 FORD MAVERICK 83 34 FORD MUSTANG 31 25 FORD NEW ESCAPE 81 43 FORD NEW RANGER 617 509 FORD TERRITORY 799 542 FORD TRANSIT VAN 237 152 HYUNDAI ACCENT 2 2 HYUNDAI ACCENT HCI 398 352 HYUNDAI ATOS AH2 326 182 HYUNDAI CRETA 17 5 HYUNDAI CRETA GRAND SU2I 68 49 HYUNDAI ELANTRA CN7 107 99 HYUNDAI GRAND I-10 346 182 HYUNDAI GRAND I-10 AI3 HB 1.2 186 150 HYUNDAI GRAND I-10 Ai3 SEDAN 49 23 HYUNDAI GRAND I-10 SEDAN 109 48 HYUNDAI H-1 3 2 HYUNDAI HD 35 371 292 HYUNDAI I20 BI3 71 45 HYUNDAI I20 IB 5 1 HYUNDAI IONIQ 6 6 HYUNDAI NEW CRETA 345 195 HYUNDAI PALISADE LX2 18 11 HYUNDAI PORTER 517 463 HYUNDAI SANTA FE TM 140 122 HYUNDAI SANTA FE TM FL 17 16 HYUNDAI SOLATI 210 160 HYUNDAI STARIA FG 12 9 HYUNDAI STARIA MB 106 81 HYUNDAI TUCSON NX4 597 5 HYUNDAI TUCSON TL 12 9 HYUNDAI VELOSTER 12 9 HYUNDAI VENUE 294 238 HYUNDAI VERNA 204 203 PEUGEOT 2008 1027 769 PEUGEOT 208 611 544 PEUGEOT 3008 1311 1009 PEUGEOT 301 591 396 PEUGEOT 308 226 11 PEUGEOT 5008 344 287 PEUGEOT BOXER 275 198 PEUGEOT EXPERT 310 210 PEUGEOT LANDTREK 509 207 PEUGEOT PARTNER 2129 1773 PEUGEOT RIFTER 202 119 PEUGEOT SIN MODELO 1 1 RENAULT ARKANA 15 13 RENAULT CLIO V 31 31 RENAULT DOKKER 64 64 RENAULT DUSTER 111 96 RENAULT EXPRESS 179 52 RENAULT KANGOO 2 2 RENAULT KOLEOS 6 6 RENAULT KWID 120 94 RENAULT OROCH 32 21 RENAULT SYMBOL 31 30 TOYOTA 4RUNNER 204 190 TOYOTA C-HR 13 8 TOYOTA COROLLA 233 176 TOYOTA COROLLA CROSS 951 655 TOYOTA FORTUNER 132 5 TOYOTA HIACE 8 6 TOYOTA HILUX 2362 1723 TOYOTA LAND CRUISER 39 28 TOYOTA PRIUS 5 4 TOYOTA RAIZE 840 467 TOYOTA RAV4 2226 1606 TOYOTA RUSH 604 467 TOYOTA TACOMA 1 1 TOYOTA YARIS 1700 1258 VOLKSWAGEN AMAROK 194 173 VOLKSWAGEN CASA RODANTE 2 2 VOLKSWAGEN GOL 1005 616 VOLKSWAGEN NIVUS 183 169 VOLKSWAGEN NUEVO VIRTUS 51 1 VOLKSWAGEN SAVEIRO 481 248 VOLKSWAGEN T-CROSS 578 471 VOLKSWAGEN TAOS 186 161 VOLKSWAGEN TIGUAN 27 21 VOLKSWAGEN VOYAGE 710 269

#**Metas para primeira semana de Setembro (pulso)**
 Neste bloco foi feita a leitura e harmonização da tabela de metas para a primeira semana de setembro, diferente da seção acima em que foi trabalhada target, que eram os dados para todo o semestre.
 A principal diferença da pulso para a target são os Dealers, que seriam filiais/lojas da concessionária. Então, sabendo os Dealers e suas quantidades vendidas de cada um podereiam ser feitas diversas consultas, como por exemplo:
 * Qual dealer vendeu mais e/ou qual vendeu menos;
 * Qual atingiu a meta e/ou qual não conseguiu alcançá-la;
 
 Além disso ainda podemos comparar os modelos, quais venderam mais, quais atingiram a meta estipulada para setembro, dentre outras.

In [0]:
#Leitura do caminho do arquivo
caminho = 'https://uniedsa.blob.core.windows.net/hudsonmesquita/1.METAS_2022_SET.xlsx'
#Leitura do Excel
metas_leitura = pd.read_excel(caminho, sheet_name='Por Dealer Real')

#Drop das linhas de espaçamento
metas_pulso = metas_leitura.dropna(how = "all")

#Obter apenas o nome do arquivo
arquivo = caminho.split('/')
nome_arquivo = arquivo[len(arquivo) - 1]

In [0]:
#Obter Data da Planilha
data = pd.to_datetime(metas_leitura.columns[2]).strftime('%Y-%m-%d')

#Retirando o nome das colunas
nome_colunas = list(metas_leitura.iloc[3].dropna())
i = nome_colunas.index('TOTAL')
del nome_colunas[i : len(nome_colunas)]


In [0]:
#Inserindo Nome das Colunas CodSAP e Modelo
nome_colunas.insert(0,"CodSAP")
nome_colunas.insert(1,"Modelo")

#Dropando colunas
metas_pulso = metas_pulso.drop([0]).drop("Unnamed: 0",axis = 1)

#Dropando as linhas de total (Retirando por Código)
metas_pulso = metas_pulso.dropna(subset = ["CONSC"])

#Renomeando colunas
metas_pulso = metas_pulso.drop([2]).rename(columns= {"CONSC":"CodSAP",data: "Modelo" })

#Tipificando corretamente a tabela CodSAP para String
metas_pulso= metas_pulso.astype({'CodSAP' : 'str'})

#Dropando as colunas de total por carro
metas_pulso = metas_pulso.dropna(axis = 1)

#Renomeação das colunas
metas_pulso.columns = nome_colunas


In [0]:
#Melt das colunas
metas_pulso = pd.melt(metas_pulso, id_vars = ["CodSAP","Modelo"])

#Renomeação da coluna de Dealers e Quantidade
metas_pulso = metas_pulso.rename(columns = {"value":"Quant","variable":"Dealer"})

#Ordenação por Modelo para reorganização
metas_pulso = metas_pulso.sort_values(["CodSAP","Dealer"])

#Reseta e organiza índice
metas_pulso = metas_pulso.reset_index()
metas_pulso = metas_pulso.drop("index", axis = 1)
metas_pulso.index += 1

#Inserindo Data na coluna
metas_pulso.insert(0,"Data", data)

#Inserindo filename na coluna
metas_pulso.insert(5,"Filename", nome_arquivo)

#Inserindo timestamp na coluna para temporização de tratamento
metas_pulso.insert(6,"Timestamp", pd.Timestamp.now())

display(metas_pulso)

Data CodSAP Modelo Dealer Quant Filename Timestamp 2022-09-11 2065 PARTNER 3.1 DL-A 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-B 16 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-C 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-D 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-E 3 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-F 9 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-G 5 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-H 10 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-I 5 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-J 1 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-K 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-L 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-M 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2065 PARTNER 3.1 DL-N 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-A 11 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-B 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-C 11 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-D 20 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-E 0 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-F 20 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-G 1 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-H 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-I 6 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-J 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-K 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-L 10 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-M 16 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2124 500 1.5 COMFORT DL-N 16 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-A 9 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-B 3 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-C 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-D 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-E 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-F 6 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-G 18 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-H 7 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-I 9 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-J 2 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-K 7 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-L 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-M 10 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2147 STARIA FG 5.SC DL-N 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2176 DUCATO DL-A 8 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2176 DUCATO DL-B 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2022-09-11 2176 DUCATO DL-C 8 1.METAS_2022_SET.xlsx 2

#**Padronização dos dados DETRAN com Pulso**

Neste bloco foi criada um **de-para** para os nomes de modelos dos dados do detran (mensais e semanais já limpos e unidos acima) e os do pulso. 

O processo **de-para** é utilizado para a obtenção de uma normalização de dados de diferentes bases a fim de ampliar as consultas e resultados que podem ser encontrados, bem como possíveis relações antes ignoradas.

In [0]:
#Leitura da tabela De-Para 
de_para = pd.read_excel('https://uniedsa.blob.core.windows.net/danielmattos/Modelo_De_Para.xlsx', sheet_name = 'Sheet1' \
                        , dtype = {'Modelo Detran' : str, 'Modelo Metas' : str }, usecols = ["Modelo Detran","Modelo Metas"])

de_para

Out[33]:

Modelo Detran 
 Modelo Metas 
 
 
 
 
 0 
 235 
 235 1L COMFORT 
 
 
 1 
 301 
 301 TM 
 
 
 2 
 420 
 420 1.8L COMFORT 
 
 
 3 
 500 1.5 COMFORT 
 500 1.5 COMFORT 
 
 
 4 
 500 1.5 LUXURY 
 500 1.5 LUXURY 
 
 
 ... 
 ... 
 ... 
 
 
 146 
 X4 
 NaN 
 
 
 147 
 X5 
 NaN 
 
 
 148 
 X6 
 NaN 
 
 
 149 
 X7 
 NaN 
 
 
 150 
 YARIS 
 NaN 
 
 
 
 151 rows × 2 columns

In [0]:
#Criação do modelo De-Para
#collect_set retorna um conjunto de objetos com elementos duplicados eliminados
modelos_detran =  sorted(dados_totais.select(f.collect_set('modelo').alias('Modelo Detran')).first()['Modelo Detran'])
modelos_pulso = sorted(metas_pulso.Modelo.unique())

#Criação e demonstração dos nomes iguais
nomes_iguais = set(modelos_detran).intersection(modelos_pulso)
print (nomes_iguais)

#Demonstração dos nomes dos modelos
print('\nModelos Detran')
print(modelos_detran)
print('\nModelos Pulso')
print(modelos_pulso)

{'DUCATO', 'N400 MAX', 'SANTA FE TM'}

Modelos Detran
['118', '2008', '208', '218I', '220', '235', '3008', '301', '308', '320', '330', '420', '430I', '4RUNNER', '5008', '520', '530', '595', 'ACCENT', 'ACCENT HCI', 'AMAROK', 'ARGO', 'ARKANA', 'ATOS AH2', 'BLAZER', 'BOXER', 'BRONCO SPORT', 'C', 'C-HR', 'CAMARO', 'CAPTIVA', 'CASA RODANTE', 'CINQUECENTO', 'CLIO V', 'COLORADO', 'CONSTELLATION', 'COROLLA', 'COROLLA CROSS', 'COUNTY', 'CRETA', 'CRETA GRAND SU2I', 'CRONOS', 'D-MAX', 'DELIVERY', 'DOKKER', 'DUCATO', 'DUSTER', 'ECOSPORT', 'EDGE', 'ELANTRA CN7', 'EX 9', 'EXPEDITION', 'EXPERT', 'EXPLORER', 'EXPRESS', 'F 350', 'F 450', 'F-150', 'F-250', 'FIORINO', 'FORTUNER', 'FTR', 'FVR', 'GOL', 'GRAND I-10', 'GRAND I-10 AI3 HB 1.2', 'GRAND I-10 Ai3 SEDAN ', 'GRAND I-10 SEDAN', 'GROOVE', 'H-1', 'HD 35', 'HIACE', 'HILUX', 'I20 BI3', 'I20 IB', 'I3', 'IONIQ', 'KANGOO', 'KOLEOS', 'KONA', 'KWID', 'LAND CRUISER', 'LANDTREK', 'MAVERICK', 'MIGHTY EX6', 'MIGHTY EX8', 'MOBI', 'MUSTANG', 'N400 MAX', 'NEW CRETA', 'NEW ESCAPE', 'NEW RANGER', 'NIVUS', 'NKR', 'NPR', 'NQR', 'NUEVO VIRTUS', 'ONIX', 'OPTRA', 'OROCH', 'PALISADE LX2', 'PARTNER', 'POLO', 'PORTER', 'PRIUS', 'PULSE', 'RAIZE', 'RAV4', 'RIFTER', 'RUSH', 'SAIL', 'SANTA FE TM', 'SANTA FE TM FL', 'SAVEIRO', 'SILVERADO', 'SIN MODELO', 'SOLATI', 'SPARK GT', 'SPIN', 'STARIA FG', 'STARIA MB', 'SUBURBAN', 'SYMBOL', 'T-CROSS', 'TACOMA', 'TAHOE', 'TAOS', 'TERRITORY', 'TIGUAN', 'TOUAREG', 'TRACKER', 'TRAILBLAZER', 'TRANSIT VAN', 'TRAVERSE', 'TUCSON NX4', 'TUCSON TL', 'VELOSTER', 'VENUE', 'VERNA', 'VOYAGE', 'X1', 'X2 ', 'X3', 'X4', 'X5', 'X6', 'X7', 'YARIS']

Modelos Pulso
['235 1L COMFORT ', '301 TM', '420 1.8L COMFORT ', '500 1.5 COMFORT', '500 1.5 LUXURY', '5008 CS', '520 1.8L COMFORT 2R', 'ARGO 4.3T', 'C-HR AC', 'DUCATO', 'ELANTRA CN7 TM', 'F-150 CS', 'MOBI SERIE C', 'N400 MAX', 'NEW ESCAPE XL EV', 'ONIX 1.3 SERIE ', 'PARTNER 3.1', 'PULSE XXL', 'SANTA FE TM', 'SANTA FE TM FL 1.0', 'SILVERADO 1.3', 'SPARK GT.4', 'STARIA FG 5.SC', 'TACOMA 1.3 TM', 'TRAILBLAZER CST']

In [0]:
#Renomeando coluna para o join
de_para = de_para.rename(columns = {'Modelo Metas' : 'Modelo'})

#Retirando o espaço dado nos valores da tabela
de_para['Modelo'] = de_para['Modelo'].str.lstrip()
de_para['Modelo Detran'] = de_para['Modelo Detran'].str.lstrip()

#Realizando o join
metas_para = metas_pulso.merge(de_para, how = 'inner')

display(metas_para)
#Drop da tabela de modelo antiga e renome para a união
metas_para = metas_para.drop(['Modelo'], axis = 1).rename(columns = {'Modelo Detran' : 'modelo'})
metas_para = metas_para[["CodSAP", "modelo", "Dealer", "Quant", "Filename", "Timestamp"]] #reordenando as colunas

#Tipificação correta da coluna modelo para String
metas_para = metas_para.astype({'modelo' : 'str'})

#Conversão da tabela metas_para de Pandas para Pyspark
metas_para = spark.createDataFrame(metas_para)
metas_para = metas_para.withColumnRenamed('modelo','Modelo')

display(metas_para)

Data CodSAP Modelo Dealer Quant Filename Timestamp Modelo Detran 2022-09-11 2065 PARTNER 3.1 DL-A 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-B 16 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-C 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-D 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-E 3 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-F 9 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-G 5 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-H 10 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-I 5 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-J 1 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-K 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-L 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-M 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2065 PARTNER 3.1 DL-N 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 PARTNER 2022-09-11 2124 500 1.5 COMFORT DL-A 11 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-B 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-C 11 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-D 20 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-E 0 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-F 20 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-G 1 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-H 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-I 6 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-J 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-K 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-L 10 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-M 16 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2124 500 1.5 COMFORT DL-N 16 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 500 1.5 COMFORT 2022-09-11 2147 STARIA FG 5.SC DL-A 9 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 5.SC DL-B 3 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 5.SC DL-C 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 5.SC DL-D 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 5.SC DL-E 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 5.SC DL-F 6 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 5.SC DL-G 18 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 5.SC DL-H 7 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 5.SC DL-I 9 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 5.SC DL-J 2 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 5.SC DL-K 7 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 STARIA FG 2022-09-11 2147 STARIA FG 

CodSAP Modelo Dealer Quant Filename Timestamp 2065 PARTNER DL-A 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-B 16 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-C 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-D 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-E 3 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-F 9 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-G 5 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-H 10 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-I 5 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-J 1 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-K 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-L 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-M 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2065 PARTNER DL-N 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-A 11 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-B 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-C 11 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-D 20 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-E 0 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-F 20 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-G 1 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-H 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-I 6 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-J 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-K 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-L 10 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-M 16 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2124 500 1.5 COMFORT DL-N 16 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-A 9 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-B 3 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-C 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-D 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-E 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-F 6 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-G 18 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-H 7 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-I 9 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-J 2 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-K 7 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-L 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-M 10 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2147 STARIA FG DL-N 17 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-A 8 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-B 13 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-C 8 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-D 12 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-E 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-F 15 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-G 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-H 1 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-I 4 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-J 19 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-K 7 1.METAS_2022_SET.xlsx 2022-09-21T22:17:14.884+0000 2176 DUCATO DL-L 2 1.METAS_2022_SE

In [0]:
#Agrupamento da tabela metas_para por modelos
metas_agg = metas_para.groupBy(['modelo']).sum().withColumnRenamed('sum(Quant)','Meta')

display(metas_agg)
#Agrupamento da tabela dados_set_totais agrupados por modelos
setembro_agg = dados_set_totais.groupBy(['modelo']).count().withColumnRenamed('count','Vendas')

display(setembro_agg)

#Junção do banco metas e dados de Setembro para verificação do atingimento da meta
metas_setembro = setembro_agg.join(metas_agg,'modelo' ,'inner')
display(metas_setembro)

#Verificação de atingimento das metas de Setembro
entrega_metas = metas_setembro.filter(col('Vendas') >= col('Meta'))
display(entrega_metas)

modelo Meta STARIA FG 128 500 1.5 COMFORT 164 520 98 DUCATO 133 ELANTRA CN7 146 235 148 PARTNER 155 PULSE 119 5008 118 TRAILBLAZER 142 MOBI 142 420 118 301 139 SILVERADO 152 F-150 170 NEW ESCAPE 128 500 1.5 LUXURY 161 N400 MAX 148 ONIX 133 SANTA FE TM 125 C-HR 104 SANTA FE TM FL 156 SPARK GT 123 ARGO 136 TACOMA 157

modelo Vendas CAMARO 1 T-CROSS 2 SILVERADO 1 GRAND I-10 AI3 HB 1.2 24 SAVEIRO 8 STARIA FG 2 308 20 COROLLA 6 STARIA MB 6 GRAND I-10 SEDAN 4 SAIL 56 CAPTIVA 22 DUSTER 4 PULSE 21 NEW CRETA 35 KWID 3 GRAND I-10 Ai3 SEDAN 9 SANTA FE TM 3 5008 3 MIGHTY EX6 1 X6 1 BRONCO SPORT 8 320 1 HILUX 97 FVR 1 EX 9 1 PORTER 11 OROCH 8 NIVUS 5 NEW ESCAPE 5 GOL 58 GROOVE 33 C-HR 1 COROLLA CROSS 29 208 5 SANTA FE TM FL 1 TOUAREG 1 NKR 1 N400 MAX 32 MUSTANG 2 VOYAGE 42 C 1 BOXER 5 4RUNNER 2 COUNTY 2 TRAILBLAZER 1 3008 12 DELIVERY 1 FTR 1 TIGUAN 1 2008 13 RAIZE 40 TAOS 2 GRAND I-10 35 MIGHTY EX8 5 EXPLORER 9 BLAZER 1 RIFTER 4 I20 BI3 6 ONIX 30 YARIS 31 LAND CRUISER 2 NEW RANGER 59 ARGO 3 CONSTELLATION 19 TERRITORY 57 DUCATO 1 ATOS AH2 16 COLORADO 35 RAV4 31 EDGE 8 TRAVERSE 2 EXPERT 7 ACCENT HCI 12 EXPRESS 21 HD 35 19 NPR 6 VENUE 15 ELANTRA CN7 1 CRETA 12 NQR 3 PARTNER 2 TRANSIT VAN 9 NUEVO VIRTUS 1 TRACKER 43 LANDTREK 18 AMAROK 2 SOLATI 6 MAVERICK 4 TUCSON NX4 16 FORTUNER 1 301 6 POLO 2 RUSH 9

modelo Vendas Meta SILVERADO 1 152 STARIA FG 2 128 PULSE 21 119 SANTA FE TM 3 125 5008 3 118 NEW ESCAPE 5 128 C-HR 1 104 SANTA FE TM FL 1 156 N400 MAX 32 148 TRAILBLAZER 1 142 ONIX 30 133 ARGO 3 136 DUCATO 1 133 ELANTRA CN7 1 146 PARTNER 2 155 301 6 139

modelo Vendas Meta

In [0]:
#Criação do modelo De-Para (Vendas Totais para Target)
modelos_detran =  sorted(dados_totais.select(f.collect_set('modelo').alias('Modelo Detran')).first()['Modelo Detran'])
modelos_target =  sorted(target.select(f.collect_set('Modelo').alias('Modelo Target')).first()['Modelo Target'])

#Verificação de igualdade de nomes
nomes_iguais = set(modelos_detran).intersection(modelos_target)
print ('Modelos Detran \n', modelos_detran)
print('\nModelos Target \n', modelos_target)

print(len(modelos_target))
print(len(nomes_iguais))

Modelos Detran 
 ['118', '2008', '208', '218I', '220', '235', '3008', '301', '308', '320', '330', '420', '430I', '4RUNNER', '5008', '520', '530', '595', 'ACCENT', 'ACCENT HCI', 'AMAROK', 'ARGO', 'ARKANA', 'ATOS AH2', 'BLAZER', 'BOXER', 'BRONCO SPORT', 'C', 'C-HR', 'CAMARO', 'CAPTIVA', 'CASA RODANTE', 'CINQUECENTO', 'CLIO V', 'COLORADO', 'CONSTELLATION', 'COROLLA', 'COROLLA CROSS', 'COUNTY', 'CRETA', 'CRETA GRAND SU2I', 'CRONOS', 'D-MAX', 'DELIVERY', 'DOKKER', 'DUCATO', 'DUSTER', 'ECOSPORT', 'EDGE', 'ELANTRA CN7', 'EX 9', 'EXPEDITION', 'EXPERT', 'EXPLORER', 'EXPRESS', 'F 350', 'F 450', 'F-150', 'F-250', 'FIORINO', 'FORTUNER', 'FTR', 'FVR', 'GOL', 'GRAND I-10', 'GRAND I-10 AI3 HB 1.2', 'GRAND I-10 Ai3 SEDAN ', 'GRAND I-10 SEDAN', 'GROOVE', 'H-1', 'HD 35', 'HIACE', 'HILUX', 'I20 BI3', 'I20 IB', 'I3', 'IONIQ', 'KANGOO', 'KOLEOS', 'KONA', 'KWID', 'LAND CRUISER', 'LANDTREK', 'MAVERICK', 'MIGHTY EX6', 'MIGHTY EX8', 'MOBI', 'MUSTANG', 'N400 MAX', 'NEW CRETA', 'NEW ESCAPE', 'NEW RANGER', 'NIVUS', 'NKR', 'NPR', 'NQR', 'NUEVO VIRTUS', 'ONIX', 'OPTRA', 'OROCH', 'PALISADE LX2', 'PARTNER', 'POLO', 'PORTER', 'PRIUS', 'PULSE', 'RAIZE', 'RAV4', 'RIFTER', 'RUSH', 'SAIL', 'SANTA FE TM', 'SANTA FE TM FL', 'SAVEIRO', 'SILVERADO', 'SIN MODELO', 'SOLATI', 'SPARK GT', 'SPIN', 'STARIA FG', 'STARIA MB', 'SUBURBAN', 'SYMBOL', 'T-CROSS', 'TACOMA', 'TAHOE', 'TAOS', 'TERRITORY', 'TIGUAN', 'TOUAREG', 'TRACKER', 'TRAILBLAZER', 'TRANSIT VAN', 'TRAVERSE', 'TUCSON NX4', 'TUCSON TL', 'VELOSTER', 'VENUE', 'VERNA', 'VOYAGE', 'X1', 'X2 ', 'X3', 'X4', 'X5', 'X6', 'X7', 'YARIS']

Modelos Target 
 ['118', '2008', '208', '218I', '220', '235', '3008', '301', '308', '320', '330', '420', '430I', '4RUNNER', '5008', '520', '530', 'ACCENT', 'ACCENT HCI', 'AMAROK', 'ARGO', 'ARKANA', 'ATOS AH2', 'BLAZER', 'BOXER', 'BRONCO SPORT', 'C-HR', 'CAMARO', 'CAPTIVA', 'CASA RODANTE', 'CINQUECENTO', 'CLIO V', 'COLORADO', 'COROLLA', 'COROLLA CROSS', 'CRETA', 'CRETA GRAND SU2I', 'CRONOS', 'D-MAX', 'DOKKER', 'DUCATO', 'DUSTER', 'ECOSPORT', 'EDGE', 'ELANTRA CN7', 'EXPEDITION', 'EXPERT', 'EXPLORER', 'EXPRESS', 'F 350', 'F 450', 'F-150', 'F-250', 'FIORINO', 'FORTUNER', 'GOL', 'GRAND I-10', 'GRAND I-10 AI3 HB 1.2', 'GRAND I-10 Ai3 SEDAN ', 'GRAND I-10 SEDAN', 'GROOVE', 'H-1', 'HD 35', 'HIACE', 'HILUX', 'I20 BI3', 'I20 IB', 'I3', 'IONIQ', 'KANGOO', 'KOLEOS', 'KWID', 'LAND CRUISER', 'LANDTREK', 'MAVERICK', 'MOBI', 'MUSTANG', 'N400 MAX', 'NEW CRETA', 'NEW ESCAPE', 'NEW RANGER', 'NIVUS', 'NUEVO VIRTUS', 'ONIX', 'OPTRA', 'OROCH', 'PALISADE LX2', 'PARTNER', 'POLO', 'PORTER', 'PRIUS', 'PULSE', 'RAIZE', 'RAV4', 'RIFTER', 'RUSH', 'SAIL', 'SANTA FE TM', 'SANTA FE TM FL', 'SAVEIRO', 'SILVERADO', 'SIN MODELO', 'SOLATI', 'SPARK GT', 'SPIN', 'STARIA FG', 'STARIA MB', 'SUBURBAN', 'SYMBOL', 'T-CROSS', 'TACOMA', 'TAHOE', 'TAOS', 'TERRITORY', 'TIGUAN', 'TRACKER', 'TRAILBLAZER', 'TRANSIT VAN', 'TRAVERSE', 'TUCSON NX4', 'TUCSON TL', 'VELOSTER', 'VENUE', 'VERNA', 'VOYAGE', 'X1', 'X2 ', 'X3', 'X4', 'X5', 'X6', 'YARIS']
132
132

#**Base de integração**

Neste bloco foi adicionado ao projeto um CSV chamado *integração* que contém os vins (indicador de venda de cada carro) e os dealers. 
Com estas informações pode-se realizar, dentre outras consultas:
* Quantidades vendidas por dealer;
* Quantidades vendidas por dealer em um intervalo de tempo, mês, por exemplo;
* Quais dealers atingiram a meta de venda mensal, semestral, anual, etc.;
* Quais dealers não atingiram as metas e em qual período.

Estas informações são essenciais para que os tomadores de decisão da empresa possam esboçar novos métodos para sanar as baixas vendas, por exemplo, e manter (ou descobrir, se ainda não tiverem tomado ciência) as estratégias que já funcionam.

In [0]:
#leitura da base de integração
integracao = spark.read.options(sep=";", header=True, encoding = "UTF-8").csv("/mnt/blobed/modulo_02/integracao/integracao.csv")

In [0]:
dados_totais_integr = integracao.join(dados_totais,['Vin'],'outer').orderBy('Data')

display(dados_totais_integr)

vin Dealer Mes Data Marca Modelo Versao MR2B29F34N1232765 DL-E 1 2022-01-03 TOYOTA YARIS YARIS SEDAN OTTO 1.5 MALBG513ANM098905 DL-I 1 2022-01-03 HYUNDAI I20 BI3 I20 BI3 1.4 8AJDB3CD5N1317042 DL-G 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 JTMZ43FV0ND104133 DL-A 1 2022-01-03 TOYOTA RAV4 RAV4 OTTO 2.0 8AJDB3CD3N1317623 DL-A 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 MALC741BAMM295803 DL-K 1 2022-01-03 HYUNDAI ACCENT HCI ACCENT HCI 1.4 8AJDB3CD2N1317550 DL-I 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 8AJDB3CD8N1317083 DL-H 1 2022-01-03 TOYOTA HILUX NEW HILUX 4X4 2.4 MALC741BAMM295811 DL-K 1 2022-01-03 HYUNDAI ACCENT HCI ACCENT HCI 1.4 MR2B29F32N1235728 DL-A 1 2022-01-03 TOYOTA YARIS YARIS SEDAN GLI 1.5 KMFAB17RPNK024484 DL-B 1 2022-01-03 HYUNDAI SOLATI H350 2.5 9BG148PK0NC431083 DL-N 1 2022-01-03 CHEVROLET COLORADO COLORADO DCAB 4X4 2.8 AT MR2B29F32N1231839 DL-D 1 2022-01-03 TOYOTA YARIS NEW YARIS 1.5 MR2B29F33N1235186 DL-J 1 2022-01-03 TOYOTA YARIS YARIS GLI 1.5 MALC741BAMM296983 DL-J 1 2022-01-03 HYUNDAI ACCENT HCI ACCENT HCI 1.4 MR2B29F3XN1234830 DL-A 1 2022-01-03 TOYOTA YARIS YARIS SEDAN OTTO 1.5 8AJDB3CD5N1317557 DL-N 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 KMFAB17RPNK024496 DL-D 1 2022-01-03 HYUNDAI SOLATI H350 2.5 8AJDB3CD0N1317076 DL-J 1 2022-01-03 TOYOTA HILUX NEW HILUX 4X4 2.4 8AJDB3CD3N1317542 DL-C 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 MR2K29F3XN1234794 DL-K 1 2022-01-03 TOYOTA YARIS YARIS HB OTTO 1.5 MALB251CANM236461 DL-D 1 2022-01-03 HYUNDAI GRAND I-10 AI3 HB 1.2 GRAND I-10 AI3 HB 1.2 VF3MCYHZUNS005824 DL-C 1 2022-01-03 PEUGEOT 3008 3008 BLUE HDI 130 EAT8 1.5 AUT 1GNSK9KDXMR463585 DL-J 1 2022-01-03 CHEVROLET SUBURBAN SUBURBAN 4X4 5.3L AUT JTEBU4JR0N5995841 DL-H 1 2022-01-03 TOYOTA 4RUNNER 4RUNNER 4X4 4.0 AUT KMFAB17RPNK024486 DL-M 1 2022-01-03 HYUNDAI SOLATI H350 2.5 KMFVA17RPNC356650 DL-E 1 2022-01-03 HYUNDAI HD 35 HD 35 LWB 2.5 VR3EF9HPANJ531924 DL-E 1 2022-01-03 PEUGEOT PARTNER PARTNER HDI 92 L1 1.6 8AJDB3CD0N1317532 DL-A 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 93Y9SR0SENJ126078 DL-N 1 2022-01-03 RENAULT OROCH OROCH ZEN MT 1.6 VR3UDYHSKNJ529068 DL-C 1 2022-01-03 PEUGEOT 2008 2008 BLUE HDI 100 4X2 1.5 KMFVA17RPNC356644 DL-C 1 2022-01-03 HYUNDAI HD 35 HD 35 LWB 2.5 8AJDB3CD5N1317607 DL-C 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 KMHYB811BNU031978 DL-C 1 2022-01-03 HYUNDAI STARIA MB STARIA US4 CRDI 2.2 AUT LZWADAGA2NG005841 DL-E 1 2022-01-03 CHEVROLET GROOVE GROOVE LTZ 1.5 VR3UPHMGBNT001463 DL-L 1 2022-01-03 PEUGEOT 208 208 PURETECH 75 1.2 8AJDB3CD9N1318064 DL-H 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 MALB241CANM096500 DL-C 1 2022-01-03 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 LZWADAGA1NG007063 DL-L 1 2022-01-03 CHEVROLET GROOVE GROOVE PREMIER 1.5 VR3UPHMGBNT001576 DL-I 1 2022-01-03 PEUGEOT 208 208 PURETECH 75 1.2 8AJDB3CD9N1317528 DL-A 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 KMHYB811BNU032004 DL-J 1 2022-01-03 HYUNDAI STARIA MB STARIA US4 CRDI 2.2 AUT 8AJCB3DDXN3908417 DL-I 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 LZWADAGA8NG006685 DL-L 1 2022-01-03 CHEVROLET GROOVE GROOVE LTZ 1.5 VR3USHNSSNJ525794 DL-J 1 2022-01-03 PEUGEOT 2008 2008 PURETECH 130 EAT8 1.2 AUT 8AJDB8CB8N5511794 DL-C 1 2022-01-03 TOYOTA HILUX HILUX PICK UP 4X4 2P 2.4 MALB241CANM096489 DL-H 1 2022-01-03 HYUNDAI GRAND I-10 SEDAN GRAND I10 SDN 1.2 WF0YXXTTGNTA25320 DL-G 1 2022-01-03 FORD TRANSIT VAN TRANSIT CUSTOM FURGON 2.2 3FMCR9B61MRB11358 DL-N 1 2022-01-03 FORD BRONCO SPORT BRONCO SPORT 1.5 LZWCDAGA1NC808169 DL-H 1 2022-01-03 CHEVROLET N400 MAX N400 MAX 1.5 8AJDB3CD8N1317617 DL-D 1 2022-01-03 TOYOTA HILUX HILUX PICKUP 4P 4X4 2.4 KMJYA371ANU029301 DL-L 1 2022-01-03 HYUNDAI STARIA MB STARIA US4 CRDI 2.2 8AJDB8CB5N5511798 DL-B 1 2022-01-03 TOYOTA HILUX HILUX PICK UP 4X4 2P 2.4 LBECBACB2NW163888 DL-J 1 2022-01-03 HYUNDAI VERNA VERNA CB 1.4 KMHYB811BNU029794 DL-F 1 2022-01-03 HYUNDAI STARIA MB STARIA US4 CRDI 2.2 AUT 1GNSK8KD7MR440677 DL-B 1 2022-01-03 CHEVROLET 

In [0]:
#Agrupamento dos modelos vendidos por dealer
totais_entrega = dados_totais_integr.groupBy(['Modelo','Dealer', 'Mes']).count() \
    .withColumnRenamed('count','Qntde_vendidas')

#Junção para averiguar atingimento da meta semestral
juncao_semestral = target.join(totais_entrega,'Modelo','inner')

#Verificação de atingimento da meta semestral
analise_semestral = juncao_semestral.filter(col('Target_Semestre_1') <= col('Qntde_vendidas')).orderBy('Dealer')

#Reorganização das colunas
analise_semestral = analise_semestral.select('Marca','Modelo','Dealer','Qntde_vendidas', 'Target_Semestre_1')

#Demonstração do resultado
display(analise_semestral)

Marca Modelo Dealer Qntde_vendidas Target_Semestre_1 BMW X1 DL-A 1 1 VOLKSWAGEN NUEVO VIRTUS DL-A 1 1 FIAT FIORINO DL-A 1 1 VOLKSWAGEN NUEVO VIRTUS DL-A 1 1 HYUNDAI TUCSON NX4 DL-A 6 5 HYUNDAI TUCSON NX4 DL-A 7 5 HYUNDAI TUCSON NX4 DL-A 7 5 HYUNDAI TUCSON NX4 DL-A 5 5 VOLKSWAGEN NUEVO VIRTUS DL-A 1 1 FORD F 450 DL-A 1 1 HYUNDAI TUCSON NX4 DL-A 6 5 HYUNDAI TUCSON NX4 DL-B 9 5 HYUNDAI TUCSON NX4 DL-B 7 5 FIAT MOBI DL-B 1 1 HYUNDAI TUCSON NX4 DL-B 9 5 VOLKSWAGEN NUEVO VIRTUS DL-B 1 1 HYUNDAI TUCSON NX4 DL-B 12 5 VOLKSWAGEN NUEVO VIRTUS DL-B 1 1 HYUNDAI TUCSON NX4 DL-B 7 5 PEUGEOT 308 DL-B 12 11 HYUNDAI TUCSON NX4 DL-C 8 5 HYUNDAI TUCSON NX4 DL-C 8 5 HYUNDAI TUCSON NX4 DL-C 5 5 VOLKSWAGEN NUEVO VIRTUS DL-C 2 1 FIAT MOBI DL-C 1 1 VOLKSWAGEN NUEVO VIRTUS DL-C 1 1 HYUNDAI TUCSON NX4 DL-C 6 5 BMW X1 DL-C 1 1 VOLKSWAGEN NUEVO VIRTUS DL-D 1 1 HYUNDAI TUCSON NX4 DL-D 6 5 BMW X1 DL-D 1 1 FIAT FIORINO DL-D 1 1 VOLKSWAGEN NUEVO VIRTUS DL-D 1 1 VOLKSWAGEN NUEVO VIRTUS DL-D 1 1 PEUGEOT SIN MODELO DL-D 1 1 VOLKSWAGEN NUEVO VIRTUS DL-D 1 1 HYUNDAI TUCSON NX4 DL-D 13 5 VOLKSWAGEN NUEVO VIRTUS DL-D 1 1 HYUNDAI TUCSON NX4 DL-D 9 5 HYUNDAI TUCSON NX4 DL-D 8 5 HYUNDAI I20 IB DL-D 1 1 HYUNDAI TUCSON NX4 DL-E 10 5 VOLKSWAGEN NUEVO VIRTUS DL-E 1 1 VOLKSWAGEN NUEVO VIRTUS DL-E 1 1 HYUNDAI TUCSON NX4 DL-E 5 5 VOLKSWAGEN NUEVO VIRTUS DL-E 3 1 CHEVROLET CAMARO DL-E 1 1 PEUGEOT 308 DL-E 14 11 BMW 430I DL-E 1 1 VOLKSWAGEN NUEVO VIRTUS DL-E 1 1 VOLKSWAGEN NUEVO VIRTUS DL-E 1 1 BMW 235 DL-E 1 1 HYUNDAI TUCSON NX4 DL-E 5 5 HYUNDAI TUCSON NX4 DL-E 5 5 VOLKSWAGEN NUEVO VIRTUS DL-F 1 1 HYUNDAI TUCSON NX4 DL-F 7 5 VOLKSWAGEN NUEVO VIRTUS DL-F 1 1 TOYOTA FORTUNER DL-F 5 5 TOYOTA TACOMA DL-F 1 1 HYUNDAI TUCSON NX4 DL-F 5 5 BMW X1 DL-F 3 1 BMW X1 DL-F 2 1 HYUNDAI TUCSON NX4 DL-F 6 5 HYUNDAI TUCSON NX4 DL-F 6 5 HYUNDAI TUCSON NX4 DL-F 7 5 HYUNDAI TUCSON NX4 DL-F 7 5 HYUNDAI TUCSON NX4 DL-G 7 5 VOLKSWAGEN NUEVO VIRTUS DL-G 2 1 HYUNDAI TUCSON NX4 DL-G 8 5 VOLKSWAGEN NUEVO VIRTUS DL-G 2 1 BMW X1 DL-G 1 1 VOLKSWAGEN NUEVO VIRTUS DL-G 1 1 HYUNDAI I20 IB DL-G 1 1 VOLKSWAGEN NUEVO VIRTUS DL-H 1 1 HYUNDAI TUCSON NX4 DL-H 8 5 HYUNDAI TUCSON NX4 DL-H 5 5 HYUNDAI TUCSON NX4 DL-H 8 5 VOLKSWAGEN NUEVO VIRTUS DL-H 1 1 VOLKSWAGEN NUEVO VIRTUS DL-H 1 1 HYUNDAI TUCSON NX4 DL-H 10 5 HYUNDAI TUCSON NX4 DL-H 5 5 CHEVROLET CAMARO DL-H 1 1 VOLKSWAGEN NUEVO VIRTUS DL-H 1 1 BMW X1 DL-H 1 1 HYUNDAI TUCSON NX4 DL-H 5 5 VOLKSWAGEN NUEVO VIRTUS DL-H 1 1 CHEVROLET OPTRA DL-H 1 1 VOLKSWAGEN NUEVO VIRTUS DL-I 1 1 HYUNDAI I20 IB DL-I 2 1 HYUNDAI TUCSON NX4 DL-I 7 5 HYUNDAI TUCSON NX4 DL-I 9 5 HYUNDAI TUCSON NX4 DL-I 5 5 HYUNDAI TUCSON NX4 DL-I 5 5 BMW X1 DL-I 1 1 VOLKSWAGEN NUEVO VIRTUS DL-I 1 1 HYUNDAI TUCSON NX4 DL-J 5 5 HYUNDAI I20 IB DL-J 1 1 HYUNDAI TUCSON NX4 DL-J 11 5 TOYOTA FORTUNER DL-J 5 5 VOLKSWAGEN NUEVO VIRTUS DL-J 2 1 BMW 530 DL-J 1 1 HYUNDAI TUCSON NX4 DL-J 5 5 VOLKSWAGEN NUEVO VIRTUS DL-J 1 1 VOLKSWAGEN NUEVO VIRTUS DL-J 1 1 HYUNDAI TUCSON NX4 DL-J 5 5 HYUNDAI TUCSON NX4 DL-K 6 5 HYUNDAI TUCSON NX4 DL-K 5 5 HYUNDAI TUCSON NX4 DL-K 11 5 VOLKSWAGEN NUEVO VIRTUS DL-K 1 1 HYUNDAI TUCSON NX4 DL-K 15 5 FIAT FIORINO DL-K 1 1 FORD F 350 DL-K 1 1 HYUNDAI TUCSON NX4 DL-K 7 5 VOLKSWAGEN NUEVO VIRTUS DL-K 1 1 HYUNDAI TUCSON NX4 DL-L 8 5 HYUNDAI TUCSON NX4 DL-L 10 5 VOLKSWAGEN NUEVO VIRTUS DL-L 1 1 HYUNDAI TUCSON NX4 DL-L 5 5 VOLKSWAGEN NUEVO VIRTUS DL-L 2 1 HYUNDAI TUCSON NX4 DL-L 7 5 VOLKSWAGEN NUEVO VIRTUS DL-L 2 1 VOLKSWAGEN NUEVO VIRTUS DL-L 1 1 PEUGEOT 308 DL-L 16 11 VOLKSWAGEN NUEVO VIRTUS DL-L 1 1 BMW X1 DL-L 1 1 HYUNDAI TUCSON NX4 DL-M 6 5 HYUNDAI TUCSON NX4 DL-M 5 5 VOLKSWAGEN NUEVO VIRTUS DL-M 2 1 HYUNDAI TUCSON NX4 DL-M 10 5 VOLKSWAGEN NUEVO VIRTUS DL-M 1 1 HYUNDAI TUCSON NX4 DL-M 6 5 HYUNDAI TUCSON NX4 DL-M 6 5 HYUNDAI TUCSON NX4 DL-M 5 5 BMW 220 DL-N 1 1 HYUNDAI TUCSON NX4 DL-N 15 5 HYUNDAI TUCSON NX4 DL-N 5 5 HYUNDAI TUCSON NX4 DL-N 8 5 VOLKSWAGEN NUEVO VIRTUS DL-N 1 1

In [0]:
#Análise mensal
juncao_mensal = target.join(totais_entrega,'Modelo','inner')

analise_mensal = juncao_mensal.filter(col('Target_Semestre_1') <= col('Qntde_vendidas')).where(col('Mes') == '9').orderBy('Dealer')

analise_mensal = analise_mensal.select('Marca','Modelo','Dealer','Qntde_vendidas', 'Target_Semestre_1')

display(analise_mensal)

Marca Modelo Dealer Qntde_vendidas Target_Semestre_1 VOLKSWAGEN NUEVO VIRTUS DL-A 1 1 CHEVROLET CAMARO DL-H 1 1